In [3]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

In [4]:
import ssl

# Отключаем проверку SSL-сертификатов
ssl._create_default_https_context = ssl._create_unverified_context

In [5]:
df = pd.read_csv('https://docs.google.com/spreadsheets/d/твой айди/export?format=csv')
df.head()

id      domain          inserted_at           updated_at  \
0   2   gmail.com  2023-06-18 08:49:07  2024-06-29 21:13:13   
1   4   gmail.com  2023-06-26 12:43:14  2025-01-13 13:51:28   
2  12  icloud.com  2023-07-22 13:09:52  2023-07-29 13:13:39   
3  14   orbita.vc  2023-08-11 14:14:32  2024-01-06 11:52:34   
4  15   gmail.com  2023-08-11 14:58:38  2023-08-18 15:03:40   

             paid_till  had trial  in_trial  canceled_subscription  \
0                  NaN       True     False                   True   
1  2025-02-04 10:23:25       True     False                  False   
2  2024-07-31 00:00:00       True      True                  False   
3                  NaN       True     False                   True   
4  2024-07-31 00:00:00       True      True                  False   

  app_version  total_paid currency_code user_agent  
0      0.9.18        56.7           EUR        NaN  
1      0.9.17       107.1           EUR        NaN  
2         NaN         0.0           EUR        NaN  
3      0.9.12        18.9           EUR        NaN  
4         NaN         0.0           EUR        NaN

In [6]:
# Преобразуем строки в формат datetime
df["inserted_at"] = pd.to_datetime(df["inserted_at"], errors="coerce")
df["updated_at"] = pd.to_datetime(df["updated_at"], errors="coerce")
df["paid_till"] = pd.to_datetime(df["paid_till"], errors="coerce")

# Проверяем результат
print(df.dtypes)

id                                int64
domain                           object
inserted_at              datetime64[ns]
updated_at               datetime64[ns]
paid_till                datetime64[ns]
had trial                          bool
in_trial                           bool
canceled_subscription              bool
app_version                      object
total_paid                      float64
currency_code                    object
user_agent                       object
dtype: object


In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     4946 non-null   int64         
 1   domain                 4946 non-null   object        
 2   inserted_at            4946 non-null   datetime64[ns]
 3   updated_at             4946 non-null   datetime64[ns]
 4   paid_till              4843 non-null   datetime64[ns]
 5   had trial              4946 non-null   bool          
 6   in_trial               4946 non-null   bool          
 7   canceled_subscription  4946 non-null   bool          
 8   app_version            3191 non-null   object        
 9   total_paid             4946 non-null   float64       
 10  currency_code          3177 non-null   object        
 11  user_agent             4381 non-null   object        
dtypes: bool(3), datetime64[ns](3), float64(1), int64(1), object(4)

In [8]:
df_presets = pd.read_csv('https://docs.google.com/spreadsheets/d/твой айди/export?format=csv')
df_presets.head()

id                      name  \
0    4      Translate to English   
1    6           Improve Writing   
2   49  Fix Spelling and Grammar   
3  120                 Summarize   
4  122              Make Shorter   

                                      system_message          inserted_at  \
0  Translate into English. Keeping formatting. No...  2023-06-01 13:39:38   
1  * Act as an assistant who revises a user's doc...  2023-06-01 14:34:42   
2  * Act as an assistant helping to revise the us...  2023-07-03 17:03:04   
3  * Act as an assistant helping to extract all f...  2023-08-10 13:57:49   
4  * Act as an assistant who helps a user write a...  2023-08-10 16:36:00   

            updated_at           hotkey  user_id  
0  2024-10-03 07:25:17  command+shift+e      NaN  
1  2024-06-10 12:46:27  command+shift+i      NaN  
2  2024-06-10 12:45:54  command+shift+l      NaN  
3  2024-06-10 12:47:23  command+shift+o      NaN  
4  2024-06-10 12:47:04              NaN      NaN

In [9]:
df_presets.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3574 entries, 0 to 3573
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0    id             3574 non-null   int64  
 1   name            3574 non-null   object 
 2   system_message  3574 non-null   object 
 3   inserted_at     3574 non-null   object 
 4   updated_at      3574 non-null   object 
 5   hotkey          1281 non-null   object 
 6   user_id         3553 non-null   float64
dtypes: float64(1), int64(1), object(5)
memory usage: 195.6+ KB


In [10]:
# Создаем копию df, чтобы не затереть оригинальные данные
df_merged = df.copy()

# Шаг 1: Убираем строки с user_id == NaN в df_presets
df_presets_filtered = df_presets.dropna(subset=["user_id"])

# Группируем только те строки, где user_id не NaN
df_presets_grouped = df_presets_filtered.groupby("user_id", as_index=False).agg({
    "system_message": lambda x: ", ".join(map(str, x))  # Объединяем system_message через запятую
})

# Логируем юзер-айди, у которых было больше одного system_message
multiple_messages = df_presets_grouped[df_presets_grouped["system_message"].str.contains(",")]
print("🔍 Пользователи с несколькими system_message:")
print(multiple_messages[["user_id", "system_message"]])

🔍 Пользователи с несколькими system_message:
      user_id                                     system_message
0         2.0  You translate to Bulgarian, make it tweet and ...
1         4.0  Add several appropriate emojis in different pa...
2        17.0  You are an expert in the topic of technology s...
3        19.0  Create a tool using GPT-4 that performs two ma...
5        28.0  * Act as an German translator, spelling correc...
...       ...                                                ...
1193   4798.0  Rewrite using varying sentence lengths- small,...
1194   4804.0  Translate into German. Keeping formatting. No ...
1195   5046.0  Debe clasificar los informes radiológicos y ad...
1197   5079.0  Vertaal naar het Nederlands. De doeltaal is Ne...
1198   5116.0  * Act as an assistant who revises a user's doc...

[983 rows x 2 columns]


In [11]:
# Фильтруем df_presets_grouped по user_id == 1270
df_filtered = df_presets_grouped[df_presets_grouped["user_id"] == 1270]

# Убираем ограничения на ширину вывода, чтобы видеть полные строки
pd.set_option("display.max_colwidth", None)

# Выводим полные строки без сокращений
df_filtered

user_id  \
161   1270.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [12]:
# Шаг 2: Объединяем df_merged и df_presets_grouped по user_id (df_presets) и id (df)
df_merged = df_merged.merge(df_presets_grouped, left_on="id", right_on="user_id", how="left")

# Шаг 3: Удаляем `user_id` после объединения, оставляем NaN для отсутствующих system_message
df_merged.drop(columns=["user_id"], inplace=True)
df_merged["system_message"].fillna(pd.NA, inplace=True)

# Проверяем результат
df_merged.head()

/var/folders/3f/yr1j00f96tn08rvm88vpmbsw0000gn/T/ipykernel_24549/2820638772.py:6: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_merged["system_message"].fillna(pd.NA, inplace=True)


id      domain         inserted_at          updated_at           paid_till  \
0   2   gmail.com 2023-06-18 08:49:07 2024-06-29 21:13:13                 NaT   
1   4   gmail.com 2023-06-26 12:43:14 2025-01-13 13:51:28 2025-02-04 10:23:25   
2  12  icloud.com 2023-07-22 13:09:52 2023-07-29 13:13:39 2024-07-31 00:00:00   
3  14   orbita.vc 2023-08-11 14:14:32 2024-01-06 11:52:34                 NaT   
4  15   gmail.com 2023-08-11 14:58:38 2023-08-18 15:03:40 2024-07-31 00:00:00   

   had trial  in_trial  canceled_subscription app_version  total_paid  \
0       True     False                   True      0.9.18        56.7   
1       True     False                  False      0.9.17       107.1   
2       True      True                  False         NaN         0.0   
3       True     False                   True      0.9.12        18.9   
4       True      True                  False         NaN         0.0   

  currency_code user_agent  \
0           EUR        NaN   
1           EUR        NaN   
2           EUR        NaN   
3           EUR        NaN   
4           EUR        NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [13]:
df_merged.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     4946 non-null   int64         
 1   domain                 4946 non-null   object        
 2   inserted_at            4946 non-null   datetime64[ns]
 3   updated_at             4946 non-null   datetime64[ns]
 4   paid_till              4843 non-null   datetime64[ns]
 5   had trial              4946 non-null   bool          
 6   in_trial               4946 non-null   bool          
 7   canceled_subscription  4946 non-null   bool          
 8   app_version            3191 non-null   object        
 9   total_paid             4946 non-null   float64       
 10  currency_code          3177 non-null   object        
 11  user_agent             4381 non-null   object        
 12  system_message         1199 non-null   object        
dtypes: 

In [14]:
df_deactivated_licenses = pd.read_csv('https://docs.google.com/spreadsheets/d/твой айди/export?format=csv')
df_deactivated_licenses.head()

id  user_id                           license_key  \
0   1    871.0  a88f3a6a-8636-4e57-8699-89f0cdcfa1a2   
1   2      NaN  4fe3acc5-60cd-4afe-97d4-023e80ab93b7   
2   3      NaN  74fca473-3fab-4500-914a-87eeba49bc6e   
3   4      NaN  b2bc5989-854e-484c-88a1-926b873e14f9   
4   5      NaN  57d987b9-db59-486a-b24c-941456a50953   

                       prev_license_key       status  tier  \
0                                   NaN  deactivated   1.0   
1                                   NaN  deactivated   1.0   
2                                   NaN  deactivated   1.0   
3  4fe3acc5-60cd-4afe-97d4-023e80ab93b7  deactivated   2.0   
4                                   NaN  deactivated   1.0   

                                                            plan_id  \
0  0690c26697af472a1b7ce4544613205e8b880626947e1393b770cdc542e92c60   
1  0690c26697af472a1b7ce4544613205e8b880626947e1393b770cdc542e92c60   
2  0690c26697af472a1b7ce4544613205e8b880626947e1393b770cdc542e92c60   
3  c4cc36c2dbedce833a1668fc598b154e72f7128eccd6a9d191eb3f7fe4150e29   
4  0690c26697af472a1b7ce4544613205e8b880626947e1393b770cdc542e92c60   

    appsumo_created_at appsumo_event_timestamp          inserted_at  \
0  2024-08-20 14:56:51     2024-08-20 14:56:51  2024-08-20 12:18:04   
1  2024-08-20 14:58:27     2024-08-20 14:58:27  2024-08-20 13:55:58   
2  2024-09-23 07:55:02     2024-09-23 07:55:02  2024-08-20 13:59:55   
3  2024-08-26 09:12:49     2024-08-26 09:12:49  2024-08-20 14:58:26   
4  2024-08-20 22:12:53     2024-08-20 22:12:53  2024-08-20 22:00:42   

            updated_at  
0  2024-08-20 14:56:52  
1  2024-08-20 14:58:27  
2  2024-09-23 07:55:02  
3  2024-08-26 09:12:49  
4  2024-08-20 22:12:54

In [15]:
df_deactivated_licenses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 813 entries, 0 to 812
Data columns (total 11 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       813 non-null    int64  
 1   user_id                  551 non-null    float64
 2   license_key              813 non-null    object 
 3   prev_license_key         55 non-null     object 
 4   status                   813 non-null    object 
 5   tier                     736 non-null    float64
 6   plan_id                  813 non-null    object 
 7   appsumo_created_at       813 non-null    object 
 8   appsumo_event_timestamp  813 non-null    object 
 9   inserted_at              813 non-null    object 
 10  updated_at               813 non-null    object 
dtypes: float64(2), int64(1), object(8)
memory usage: 70.0+ KB


In [16]:
df_deactivated_licenses_revoke = pd.read_csv('https://docs.google.com/spreadsheets/d/твой айди/export?format=csv')
df_deactivated_licenses_revoke.head()

license_key                     purchase_date  \
0  c1d9fe1c-18a4-41db-a6f0-e82fc2f6cdbb  2024-10-05 03:37:52.358821+00:00   
1  142929c2-c11d-484b-859c-1c977bfdbe56  2024-10-05 04:51:17.872774+00:00   
2  69ba430e-ba76-40e1-a136-646992afb44d  2024-10-09 04:01:54.343270+00:00   
3  6e331ec7-edd9-435e-bbfe-8d2eab572faf  2024-10-05 04:51:17.894860+00:00   
4  b4927853-5c39-4917-8616-ec8d44c17ed7  2024-10-06 04:37:22.958954+00:00   

                        refund_date  \
0  2024-11-06 08:49:49.715708+00:00   
1  2024-11-20 13:26:33.445351+00:00   
2  2024-11-04 15:25:59.042299+00:00   
3  2024-11-20 13:25:59.487680+00:00   
4  2024-10-06 13:23:44.540606+00:00   

                                       reason  \
0                                       Other   
1                                       Other   
2  Product was difficult to use or understand   
3                                       Other   
4                            No longer needed   

                                                                                                                                                                                              feedback  
0                                                                              Simple reason \nIt just never worked on my Mac. \nI did emailed pismo but never got any respond  So \n I gave up trying  
1  I think this is a great product. I would love to be able to use voice dictation, for instance. For now, AutoHotkey and ChatGPT have given me the AI auto-correction I need, with a 0.01 daily cost.  
2                                                                                                                                                                         Was not alle to use properly  
3  I think this is a great product. I would love to be able to use voice dictation, for instance. For now, AutoHotkey and ChatGPT have given me the AI auto-correction I need, with a 0.01 daily cost.  
4                                                                                                                                                                                      purchased twice

In [17]:
df_deactivated_licenses_revoke.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 712 entries, 0 to 711
Data columns (total 5 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   license_key    712 non-null    object
 1   purchase_date  712 non-null    object
 2   refund_date    705 non-null    object
 3   reason         695 non-null    object
 4   feedback       672 non-null    object
dtypes: object(5)
memory usage: 27.9+ KB


In [18]:
# Удаляем только одну лишнюю строку с этим license_key
df_deactivated_licenses_revoke = df_deactivated_licenses_revoke[df_deactivated_licenses_revoke.duplicated(subset=["license_key"], keep="first") == False]

# Проверяем, что дубликата больше нет
df_deactivated_licenses_revoke[df_deactivated_licenses_revoke["license_key"] == "bb006b29-6f9b-4fa8-b912-c375bbdf081c"]

license_key                     purchase_date  \
664  bb006b29-6f9b-4fa8-b912-c375bbdf081c  2024-11-14 04:47:55.464409+00:00   

                          refund_date            reason feedback  
664  2024-12-11 04:11:07.960087+00:00  No longer needed       Na

In [19]:
# Создаем копию, чтобы не менять оригинальный DataFrame
df_deactivated_licenses_updated = df_deactivated_licenses.copy()

# Преобразуем df_deactivated_licenses_revoke в словарь для быстрого поиска
revoke_dict = df_deactivated_licenses_revoke.set_index("license_key")[["reason", "feedback"]].to_dict("index")

# Проходимся по каждой строке в df_deactivated_licenses и добавляем reason и feedback
for i, row in df_deactivated_licenses_updated.iterrows():
    license_key = row["license_key"]
    prev_license_key = row["prev_license_key"]

    # Проверяем, есть ли license_key в revoke_dict
    if license_key in revoke_dict:
        df_deactivated_licenses_updated.at[i, "reason"] = revoke_dict[license_key]["reason"]
        df_deactivated_licenses_updated.at[i, "feedback"] = revoke_dict[license_key]["feedback"]
    # Если не нашли, ищем по prev_license_key
    elif prev_license_key in revoke_dict:
        df_deactivated_licenses_updated.at[i, "reason"] = revoke_dict[prev_license_key]["reason"]
        df_deactivated_licenses_updated.at[i, "feedback"] = revoke_dict[prev_license_key]["feedback"]

# Выводим структуру обновленного DataFrame
df_deactivated_licenses_updated.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 813 entries, 0 to 812
Data columns (total 13 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       813 non-null    int64  
 1   user_id                  551 non-null    float64
 2   license_key              813 non-null    object 
 3   prev_license_key         55 non-null     object 
 4   status                   813 non-null    object 
 5   tier                     736 non-null    float64
 6   plan_id                  813 non-null    object 
 7   appsumo_created_at       813 non-null    object 
 8   appsumo_event_timestamp  813 non-null    object 
 9   inserted_at              813 non-null    object 
 10  updated_at               813 non-null    object 
 11  reason                   677 non-null    object 
 12  feedback                 654 non-null    object 
dtypes: float64(2), int64(1), object(10)
memory usage: 82.7+ KB


In [20]:
df_deactivated_licenses_updated.to_pickle("/Users/user/Pismo/df_deactivated_licenses_updated.pkl")

In [21]:
df_merged.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     4946 non-null   int64         
 1   domain                 4946 non-null   object        
 2   inserted_at            4946 non-null   datetime64[ns]
 3   updated_at             4946 non-null   datetime64[ns]
 4   paid_till              4843 non-null   datetime64[ns]
 5   had trial              4946 non-null   bool          
 6   in_trial               4946 non-null   bool          
 7   canceled_subscription  4946 non-null   bool          
 8   app_version            3191 non-null   object        
 9   total_paid             4946 non-null   float64       
 10  currency_code          3177 non-null   object        
 11  user_agent             4381 non-null   object        
 12  system_message         1199 non-null   object        
dtypes: 

In [22]:
df_merged_updated = df_merged.merge(
    df_deactivated_licenses_updated[['user_id', 'tier', 'reason', 'feedback']],
    left_on='id', right_on='user_id', how='left'
).drop(columns=['user_id'])  # Убираем дублирующийся столбец user_id

# Сохраняем новую таблицу в pkl
# df_merged_updated.to_pickle("/Users/user/Pismo/df_merged_updated.pkl")

In [23]:
df_merged_updated.head()


id      domain         inserted_at          updated_at           paid_till  \
0   2   gmail.com 2023-06-18 08:49:07 2024-06-29 21:13:13                 NaT   
1   4   gmail.com 2023-06-26 12:43:14 2025-01-13 13:51:28 2025-02-04 10:23:25   
2  12  icloud.com 2023-07-22 13:09:52 2023-07-29 13:13:39 2024-07-31 00:00:00   
3  14   orbita.vc 2023-08-11 14:14:32 2024-01-06 11:52:34                 NaT   
4  15   gmail.com 2023-08-11 14:58:38 2023-08-18 15:03:40 2024-07-31 00:00:00   

   had trial  in_trial  canceled_subscription app_version  total_paid  \
0       True     False                   True      0.9.18        56.7   
1       True     False                  False      0.9.17       107.1   
2       True      True                  False         NaN         0.0   
3       True     False                   True      0.9.12        18.9   
4       True      True                  False         NaN         0.0   

  currency_code user_agent  \
0           EUR        NaN   
1           EUR        NaN   
2           EUR        NaN   
3           EUR        NaN   
4           EUR        NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [24]:
# Вывести все email-адреса и их id
df_emails = df_merged_updated[["id", "domain"]]
df_emails


id       domain
0        2    gmail.com
1        4    gmail.com
2       12   icloud.com
3       14    orbita.vc
4       15    gmail.com
...    ...          ...
4941  5122      aol.com
4942  5123  hotmail.com
4943  5124    gmail.com
4944  5125    gmail.com
4945  5126  hotmail.com

[4946 rows x 2 columns]

In [30]:
import pandas as pd
import time
from user_agents import parse
import openai
import langdetect

# ✅ API OpenAI (ключ подставить вручную)
client = openai.OpenAI(api_key="твой апи")

In [27]:
df_merged_updated.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 16 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     4946 non-null   int64         
 1   domain                 4946 non-null   object        
 2   inserted_at            4946 non-null   datetime64[ns]
 3   updated_at             4946 non-null   datetime64[ns]
 4   paid_till              4843 non-null   datetime64[ns]
 5   had trial              4946 non-null   bool          
 6   in_trial               4946 non-null   bool          
 7   canceled_subscription  4946 non-null   bool          
 8   app_version            3191 non-null   object        
 9   total_paid             4946 non-null   float64       
 10  currency_code          3177 non-null   object        
 11  user_agent             4381 non-null   object        
 12  system_message         1199 non-null   object        
 13  tie

In [31]:
import time
from user_agents import parse

# ✅ Функция для исправления доменов (заменяет данные в той же колонке)
def correct_domain(domain):
    if pd.isna(domain):
        return domain  # Если пусто, оставляем как есть
    
    messages = [
        {"role": "system", "content": "You are an AI that corrects email domains."},
        {"role": "user", "content": f"Fix any spelling errors in the following email domain: {domain}. If it is correct, return it unchanged."}
    ]

    while True:
        try:
            response = client.chat.completions.create(
                model="gpt-3.5-turbo",
                messages=messages,
                max_tokens=10,
                temperature=0,
            )
            corrected_domain = response.choices[0].message.content.strip()

            # ✅ ВАЖНО: Если домен корректный, API не должен ничего дописывать
            if corrected_domain.lower() == domain.lower():
                return domain
            return corrected_domain
        except openai.RateLimitError:
            print("⚠️ API Rate Limit! Ждем 60 секунд...")
            time.sleep(60)
        except Exception as e:
            print(f"❌ Ошибка API: {e}")
            return domain  # Возвращаем исходное, если ошибка

# ✅ Функция для определения браузера и ОС
def parse_user_agent(user_agent):
    if pd.isna(user_agent):
        return pd.Series([None, None])  # Если user_agent пустой, возвращаем None
    
    parsed = parse(user_agent)
    return pd.Series([parsed.browser.family, parsed.os.family])

# ✅ Создаем `df_merged_updated_dom_braus_os` на основе `df_merged_updated`
df_merged_updated_dom_braus_os = df_merged_updated.copy()

# 🔹 **Обновление домена (исправление опечаток, но без изменений корректных значений)**
batch_size = 50
for start in range(0, len(df_merged_updated_dom_braus_os), batch_size):
    end = min(start + batch_size, len(df_merged_updated_dom_braus_os))
    print(f"🚀 Обрабатываем домены: строки {start} - {end}...")
    df_merged_updated_dom_braus_os.loc[start:end, 'domain'] = df_merged_updated_dom_braus_os.loc[start:end, 'domain'].apply(correct_domain)

# 🔹 **Определение браузера и ОС**
df_merged_updated_dom_braus_os[['browser', 'os']] = df_merged_updated_dom_braus_os['user_agent'].apply(parse_user_agent)

# ✅ Выводим количество уникальных значений в новых колонках
print("✅ Уникальные значения в новых колонках:")
print("Browser:", df_merged_updated_dom_braus_os['browser'].nunique())
print("OS:", df_merged_updated_dom_braus_os['os'].nunique())

🚀 Обрабатываем домены: строки 0 - 50...
🚀 Обрабатываем домены: строки 50 - 100...
🚀 Обрабатываем домены: строки 100 - 150...
🚀 Обрабатываем домены: строки 150 - 200...
🚀 Обрабатываем домены: строки 200 - 250...
🚀 Обрабатываем домены: строки 250 - 300...
🚀 Обрабатываем домены: строки 300 - 350...
🚀 Обрабатываем домены: строки 350 - 400...
🚀 Обрабатываем домены: строки 400 - 450...
🚀 Обрабатываем домены: строки 450 - 500...
🚀 Обрабатываем домены: строки 500 - 550...
🚀 Обрабатываем домены: строки 550 - 600...
🚀 Обрабатываем домены: строки 600 - 650...
🚀 Обрабатываем домены: строки 650 - 700...
🚀 Обрабатываем домены: строки 700 - 750...
🚀 Обрабатываем домены: строки 750 - 800...
🚀 Обрабатываем домены: строки 800 - 850...
🚀 Обрабатываем домены: строки 850 - 900...
🚀 Обрабатываем домены: строки 900 - 950...
🚀 Обрабатываем домены: строки 950 - 1000...
🚀 Обрабатываем домены: строки 1000 - 1050...
🚀 Обрабатываем домены: строки 1050 - 1100...
🚀 Обрабатываем домены: строки 1100 - 1150...
🚀 Обраба

In [33]:
df_merged_updated_dom_braus_os.head()

id                                    domain         inserted_at  \
0   2  The email domain "gmail.com" is correct. 2023-06-18 08:49:07   
1   4  The email domain "gmail.com" is correct. 2023-06-26 12:43:14   
2  12  The email domain "icloud.com" is correct 2023-07-22 13:09:52   
3  14           The email domain "orbita.vc" is 2023-08-11 14:14:32   
4  15  The email domain "gmail.com" is correct. 2023-08-11 14:58:38   

           updated_at           paid_till  had trial  in_trial  \
0 2024-06-29 21:13:13                 NaT       True     False   
1 2025-01-13 13:51:28 2025-02-04 10:23:25       True     False   
2 2023-07-29 13:13:39 2024-07-31 00:00:00       True      True   
3 2024-01-06 11:52:34                 NaT       True     False   
4 2023-08-18 15:03:40 2024-07-31 00:00:00       True      True   

   canceled_subscription app_version  total_paid currency_code user_agent  \
0                   True      0.9.18        56.7           EUR        NaN   
1                  False      0.9.17       107.1           EUR        NaN   
2                  False         NaN         0.0           EUR        NaN   
3                   True      0.9.12        18.9           EUR        NaN   
4                  False         NaN         0.0           EUR        NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [36]:
# ✅ Функция для выделения только домена из текста
def extract_domain(text):
    if pd.isna(text) or text.strip() == "":
        return None  # Пропускаем пустые строки
    
    messages = [
        {"role": "system", "content": "You are an AI that extracts only the domain name from a given text. Return only the domain, nothing else."},
        {"role": "user", "content": f"Extract the domain from this text: {text}. Return only the domain, without 'http://', 'https://', 'www.' or any extra words."}
    ]

    while True:
        try:
            response = client.chat.completions.create(
                model="gpt-3.5-turbo",
                messages=messages,
                max_tokens=20,
                temperature=0,
            )
            extracted_domain = response.choices[0].message.content.strip()

            # ✅ Убираем лишние пробелы и проверяем, что ответ - это именно домен
            extracted_domain = extracted_domain.split()[0].strip()

            return extracted_domain
        except openai.RateLimitError:
            print("⚠️ API Rate Limit! Ждем 60 секунд...")
            time.sleep(60)
        except Exception as e:
            print(f"❌ Ошибка API: {e}")
            return None  # Если ошибка, оставляем пустым

# ✅ Запускаем обработку всей таблицы (разбиваем на батчи)
batch_size = 50
total_rows = len(df_merged_updated_dom_braus_os)

for start in range(0, total_rows, batch_size):
    end = min(start + batch_size, total_rows)
    print(f"🚀 Обрабатываем строки {start} - {end}...")
    df_merged_updated_dom_braus_os.loc[start:end, 'domain'] = df_merged_updated_dom_braus_os.loc[start:end, 'domain'].apply(extract_domain)

print("✅ Обработка завершена! Проверь результаты:")
print(df_merged_updated_dom_braus_os.head(50))

🚀 Обрабатываем строки 0 - 50...
🚀 Обрабатываем строки 50 - 100...
🚀 Обрабатываем строки 100 - 150...
🚀 Обрабатываем строки 150 - 200...
🚀 Обрабатываем строки 200 - 250...
🚀 Обрабатываем строки 250 - 300...
🚀 Обрабатываем строки 300 - 350...
🚀 Обрабатываем строки 350 - 400...
🚀 Обрабатываем строки 400 - 450...
🚀 Обрабатываем строки 450 - 500...
🚀 Обрабатываем строки 500 - 550...
🚀 Обрабатываем строки 550 - 600...
🚀 Обрабатываем строки 600 - 650...
🚀 Обрабатываем строки 650 - 700...
🚀 Обрабатываем строки 700 - 750...
🚀 Обрабатываем строки 750 - 800...
🚀 Обрабатываем строки 800 - 850...
🚀 Обрабатываем строки 850 - 900...
🚀 Обрабатываем строки 900 - 950...
🚀 Обрабатываем строки 950 - 1000...
🚀 Обрабатываем строки 1000 - 1050...
🚀 Обрабатываем строки 1050 - 1100...
🚀 Обрабатываем строки 1100 - 1150...
🚀 Обрабатываем строки 1150 - 1200...
🚀 Обрабатываем строки 1200 - 1250...
🚀 Обрабатываем строки 1250 - 1300...
🚀 Обрабатываем строки 1300 - 1350...
🚀 Обрабатываем строки 1350 - 1400...
🚀 Обраб

In [37]:
df_merged_updated_dom_braus_os.to_csv("df_merged_updated_dom_braus_os.csv", index=False)
print("✅ Промежуточные данные сохранены в df_merged_updated_dom_braus_os.csv")

✅ Промежуточные данные сохранены в df_merged_updated_dom_braus_os.csv


In [38]:
df_merged_updated_2 = pd.read_csv("df_merged_updated_dom_braus_os.csv")
print("✅ Данные загружены из df_merged_updated_dom_braus_os.csv")

✅ Данные загружены из df_merged_updated_dom_braus_os.csv


In [39]:
# ✅ Функция для классификации домена (определяет, публичный или корпоративный)
def classify_domain(domain):
    if pd.isna(domain) or domain.strip() == "":
        return None, None, None  # Если пусто, оставляем все поля пустыми

    messages = [
        {"role": "system", "content": "You are an AI that checks whether an email domain is corporate or public."},
        {"role": "user", "content": f"Is {domain} a public email provider like Gmail, Yahoo, Outlook, Mail.ru, or a corporate domain? Respond with 'public' or 'corporate'."}
    ]

    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=10,
            temperature=0,
        )
        domain_type = response.choices[0].message.content.strip().lower()

        if domain_type == "public":
            return None, None, None  # Публичный домен → оставляем поля пустыми
        
        # Запрос на определение компании, сектора и страны
        messages = [
            {"role": "system", "content": "You are an AI that classifies corporate email domains and identifies company details."},
            {"role": "user", "content": f"Analyze the corporate email domain {domain}. Return the company name, business sector, and country in the format: Company - Sector - Country. If unknown, return 'Unknown - Unknown - Unknown'."}
        ]
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=50,
            temperature=0,
        )
        result = response.choices[0].message.content.strip()

        # Разделяем строку на Company - Sector - Country
        parts = result.split(" - ")
        if len(parts) == 3:
            return parts[0], parts[1], parts[2]
        return "Unknown", "Unknown", "Unknown"

    except openai.RateLimitError:
        print("⚠️ API Rate Limit! Ждем 60 секунд...")
        time.sleep(60)
        return None, None, None

    except Exception as e:
        print(f"❌ Ошибка API: {e}")
        return None, None, None  # Оставляем пустым, если ошибка

# ✅ Создаем новый DataFrame для обработки
df_merged_updated_comp_sect_comcountry = df_merged_updated_2.copy()

# ✅ Обновляем колонки `company`, `sector` и `company_country`
batch_size = 50
total_rows = len(df_merged_updated_comp_sect_comcountry)

for start in range(0, total_rows, batch_size):
    end = min(start + batch_size, total_rows)
    print(f"🚀 Обрабатываем строки {start} - {end}...")
    
    df_merged_updated_comp_sect_comcountry.loc[start:end, ['company', 'sector', 'company_country']] = df_merged_updated_comp_sect_comcountry.loc[start:end, 'domain'].apply(lambda x: pd.Series(classify_domain(x)))

# ✅ Сохраняем обработанный DataFrame в CSV
df_merged_updated_comp_sect_comcountry.to_csv("df_merged_updated_comp_sect_comcountry.csv", index=False)
print("✅ Данные сохранены в df_merged_updated_comp_sect_comcountry.csv")

# ✅ Проверяем первые 50 строк
print(df_merged_updated_comp_sect_comcountry.head(50))

🚀 Обрабатываем строки 0 - 50...
🚀 Обрабатываем строки 50 - 100...
🚀 Обрабатываем строки 100 - 150...
🚀 Обрабатываем строки 150 - 200...
🚀 Обрабатываем строки 200 - 250...
🚀 Обрабатываем строки 250 - 300...
🚀 Обрабатываем строки 300 - 350...
🚀 Обрабатываем строки 350 - 400...
🚀 Обрабатываем строки 400 - 450...
🚀 Обрабатываем строки 450 - 500...
🚀 Обрабатываем строки 500 - 550...
🚀 Обрабатываем строки 550 - 600...
🚀 Обрабатываем строки 600 - 650...
🚀 Обрабатываем строки 650 - 700...
🚀 Обрабатываем строки 700 - 750...
🚀 Обрабатываем строки 750 - 800...
🚀 Обрабатываем строки 800 - 850...
🚀 Обрабатываем строки 850 - 900...
🚀 Обрабатываем строки 900 - 950...
🚀 Обрабатываем строки 950 - 1000...
🚀 Обрабатываем строки 1000 - 1050...
🚀 Обрабатываем строки 1050 - 1100...
🚀 Обрабатываем строки 1100 - 1150...
🚀 Обрабатываем строки 1150 - 1200...
🚀 Обрабатываем строки 1200 - 1250...
🚀 Обрабатываем строки 1250 - 1300...
🚀 Обрабатываем строки 1300 - 1350...
🚀 Обрабатываем строки 1350 - 1400...
🚀 Обраб

In [ ]:
# ✅ Функция для определения, корпоративный или публичный домен
def check_domain_type(domain):
    if pd.isna(domain) or domain.strip() == "":
        return "unknown"  # Если пусто, оставляем неизвестным

    messages = [
        {"role": "system", "content": "You are an AI that checks whether an email domain is corporate or public."},
        {"role": "user", "content": f"Is {domain} a public email provider like Gmail, Yahoo, Outlook, Mail.ru, or a corporate domain? Respond with ONLY 'public' or 'corporate'. Do not add any extra text."}
    ]

    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=10,
            temperature=0,
        )
        domain_type = response.choices[0].message.content.strip().lower()

        # ✅ Оставляем только четкие ответы "public" или "corporate"
        if "public" in domain_type:
            return "public"
        elif "corporate" in domain_type:
            return "corporate"
        else:
            return "unknown"  # Если API вернул что-то непонятное

    except Exception as e:
        print(f"❌ Ошибка API: {e}")
        return "unknown"

# ✅ Тестируем снова на 5 случайных доменах
test_domains = df_merged_updated_2['domain'].dropna().sample(5).tolist()

for domain in test_domains:
    domain_type = check_domain_type(domain)
    print(f"🌍 Домен: {domain} → Тип: {domain_type}")


In [ ]:
# ✅ Функция для определения, корпоративный или публичный домен
def check_domain_type(domain):
    if pd.isna(domain) or domain.strip() == "":
        return "unknown"  # Если пусто, оставляем неизвестным

    messages = [
        {"role": "system", "content": "You are an AI that checks whether an email domain is corporate or public."},
        {"role": "user", "content": f"Is {domain} a public email provider like Gmail, Yahoo, Outlook, Mail.ru, or a corporate domain? Respond with ONLY 'public' or 'corporate'. Do not add any extra text."}
    ]

    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=10,
            temperature=0,
        )
        domain_type = response.choices[0].message.content.strip().lower()

        # ✅ Оставляем только четкие ответы "public" или "corporate"
        if "public" in domain_type:
            return "public"
        elif "corporate" in domain_type:
            return "corporate"
        else:
            return "unknown"  # Если API вернул что-то непонятное

    except Exception as e:
        print(f"❌ Ошибка API: {e}")
        return "unknown"

# ✅ Тестируем снова на 5 случайных доменах
test_domains = df_merged_updated_2['domain'].dropna().sample(5).tolist()

for domain in test_domains:
    domain_type = check_domain_type(domain)
    print(f"🌍 Домен: {domain} → Тип: {domain_type}")

In [ ]:
def check_domain_type(domain):
    if pd.isna(domain) or domain.strip() == "":
        return "unknown"  # Если пусто, оставляем неизвестным

    messages = [
        {"role": "system", "content": "You are an AI that checks whether an email domain is corporate or public."},
        {"role": "user", "content": f"Is {domain} a public email provider like Gmail, Yahoo, Outlook, Mail.ru, or a corporate domain? Respond with ONLY 'public' or 'corporate'. Do not add any extra text."}
    ]

    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=10,
            temperature=0,
        )
        domain_type = response.choices[0].message.content.strip().lower()

        # ✅ Если API вернул что-то странное, оставляем "unknown"
        if domain_type not in ["public", "corporate"]:
            return "unknown"

        return domain_type

    except Exception as e:
        print(f"❌ Ошибка API: {e}")
        return "unknown"

# ✅ Перезапускаем обработку ТОЛЬКО для странных доменов (например, `public`, но явно не публичный)
df_merged_updated_2.loc[df_merged_updated_2['domain_type'] == 'public', 'domain_type'] = \
    df_merged_updated_2.loc[df_merged_updated_2['domain_type'] == 'public', 'domain'].apply(check_domain_type)

print("✅ Повторная проверка завершена!")

In [53]:
# ✅ Сколько строк с "public" под пересмотр
public_count = df_merged_updated_2[df_merged_updated_2['domain_type'] == 'public'].shape[0]
print(f"📌 Количество строк для повторной проверки: {public_count}")

📌 Количество строк для повторной проверки: 47


In [54]:
df_merged_updated_2.loc[df_merged_updated_2['domain_type'] == 'public', 'domain_type'] = \
    df_merged_updated_2.loc[df_merged_updated_2['domain_type'] == 'public', 'domain'].apply(check_domain_type)

print("✅ Повторная проверка завершена!")

✅ Повторная проверка завершена!


In [55]:
print(df_merged_updated_2[df_merged_updated_2['domain_type'] == 'public'][['domain', 'domain_type']])

               domain domain_type
0           gmail.com      public
1           gmail.com      public
2          icloud.com      public
4           gmail.com      public
5           gmail.com      public
6           gmail.com      public
7           yahoo.com      public
8               3f.lu      public
9           gmail.com      public
10        outlook.com      public
11              pm.me      public
13          gmail.com      public
14  zentrapreneur.com      public
15          gmail.com      public
16          yandex.ru      public
17          gmail.com      public
18          yahoo.com      public
19          gmail.com      public
20          gmail.com      public
21    sadadasdsad.com      public
22          gmail.com      public
23          gmail.com      public
24          gmail.com      public
25          gmail.com      public
26          gmail.com      public
27          gmail.com      public
28          gmail.com      public
29          gmail.com      public
30          gm

In [56]:
# ✅ Доверенные публичные домены (которые API не должен путать)
trusted_public_domains = {"gmail.com", "yahoo.com", "mail.ru", "icloud.com", "outlook.com", "pm.me", "yandex.ru"}

# ✅ Проверяем только странные случаи
def fix_wrong_public_domains(domain, domain_type):
    if domain_type == "public" and domain not in trusted_public_domains:
        return "unknown"  # Если `public`, но его нет в списке – меняем на `unknown`
    return domain_type

df_merged_updated_2['domain_type'] = df_merged_updated_2.apply(
    lambda row: fix_wrong_public_domains(row['domain'], row['domain_type']), axis=1
)

print("✅ Ошибки исправлены!")

✅ Ошибки исправлены!


In [57]:
print(df_merged_updated_2[df_merged_updated_2['domain_type'] == 'public'][['domain', 'domain_type']])

         domain domain_type
0     gmail.com      public
1     gmail.com      public
2    icloud.com      public
4     gmail.com      public
5     gmail.com      public
6     gmail.com      public
7     yahoo.com      public
9     gmail.com      public
10  outlook.com      public
11        pm.me      public
13    gmail.com      public
15    gmail.com      public
16    yandex.ru      public
17    gmail.com      public
18    yahoo.com      public
19    gmail.com      public
20    gmail.com      public
22    gmail.com      public
23    gmail.com      public
24    gmail.com      public
25    gmail.com      public
26    gmail.com      public
27    gmail.com      public
28    gmail.com      public
29    gmail.com      public
30    gmail.com      public
31    gmail.com      public
32    gmail.com      public
33    gmail.com      public
34    gmail.com      public
35      mail.ru      public
37    gmail.com      public
38    gmail.com      public
39    gmail.com      public
41    gmail.com     

In [59]:
df_merged_updated_2.loc[df_merged_updated_2['domain_type'].isna(), 'domain_type'] = \
    df_merged_updated_2.loc[df_merged_updated_2['domain_type'].isna(), 'domain'].apply(check_domain_type)

print("✅ Все `NaN` обработаны!")

✅ Все `NaN` обработаны!


In [60]:
missing_count = df_merged_updated_2['domain_type'].isna().sum()
print(f"📌 Количество необработанных строк: {missing_count}")

📌 Количество необработанных строк: 0


In [61]:
print(df_merged_updated_2['domain_type'].value_counts())

domain_type
public       4218
corporate     724
unknown         4
Name: count, dtype: int64


In [62]:
# Уникальные `public` домены
unique_public = df_merged_updated_2[df_merged_updated_2['domain_type'] == 'public']['domain'].unique()
print(f"📌 Уникальные `public` домены ({len(unique_public)}):\n{', '.join(unique_public)}\n")

# Уникальные `corporate` домены
unique_corporate = df_merged_updated_2[df_merged_updated_2['domain_type'] == 'corporate']['domain'].unique()
print(f"🏢 Уникальные `corporate` домены ({len(unique_corporate)}):\n{', '.join(unique_corporate)}\n")

# Уникальные `unknown` домены
unique_unknown = df_merged_updated_2[df_merged_updated_2['domain_type'] == 'unknown']['domain'].unique()
print(f"❓ Уникальные `unknown` домены ({len(unique_unknown)}):\n{', '.join(unique_unknown)}\n")

📌 Уникальные `public` домены (519):
gmail.com, icloud.com, yahoo.com, outlook.com, pm.me, yandex.ru, mail.ru, inbox.ru, te.st, proton.me, list.ru, mailinator.com, jeremyblaze.com, qq.com, jaroslavski.ee, 1214.com, google.com, mail.com, yopmail.com, hotmail.com, tutoreve.com, linuxmail.org, me.com, etopys.com, abnovel.com, fgrsegsg.com, test.test, test.com, funvane.com, ya.ru, protonmail.com, jollyfree.com, seturon.io, luaravel, saltdalkomm, kvasnikoff.com, nolanzip.com, hjeen.com, scl.gov.in, calunia.com, carspure.com, pobox.com, telus.net, gmail, yahoo.ca, t-online.de, yahoo.co.uk, seznam.cz, web.de, ibnews.com.au, mostgames.org, themostgames.org, appsumo.com, teleg.eu, winterkids.org, techguru.pro, googlemail.com, renaybloom.com, xmission.com, aclevercat.com, laclear.us, beeble.com, postbox.day, connysoderholm.com, lock.email, maildepot.net, maximo-seo.com, yahoo.co.jp, velvet-mag.lat, grages.de, nami.space, labrujita.es, 126.com, trumanpress.us, thechristianchain.org, balog.ro, live

In [63]:
# Обновляем `unknown` домены в `corporate`
df_merged_updated_2.loc[df_merged_updated_2['domain'].isin(["3f.lu", "zentrapreneur.com"]), "domain_type"] = "corporate"

print("✅ Исправлено: `3f.lu` и `zentrapreneur.com` теперь `corporate`")

✅ Исправлено: `3f.lu` и `zentrapreneur.com` теперь `corporate`


In [64]:
print(df_merged_updated_2[df_merged_updated_2['domain'].isin(["3f.lu", "zentrapreneur.com"])][['domain', 'domain_type']])

                 domain domain_type
8                 3f.lu   corporate
14    zentrapreneur.com   corporate
4091              3f.lu   corporate


In [65]:
# ✅ Переводим `duck.com`, `hey.com`, `mozmail.com`, `zoho.com` в `public`
wrong_corporate = ["duck.com", "hey.com", "mozmail.com", "zoho.com"]
df_merged_updated_2.loc[df_merged_updated_2['domain'].isin(wrong_corporate), "domain_type"] = "public"

print("✅ Исправлены спорные домены: переведены обратно в `public`")

✅ Исправлены спорные домены: переведены обратно в `public`


In [66]:
print(df_merged_updated_2[df_merged_updated_2['domain'].isin(wrong_corporate)][['domain', 'domain_type']])

           domain domain_type
124      duck.com      public
613      duck.com      public
1051     duck.com      public
1126     duck.com      public
1580     duck.com      public
1878  mozmail.com      public
1917     duck.com      public
2040     zoho.com      public
2184      hey.com      public
2689     duck.com      public
2723     duck.com      public
4359     duck.com      public
4440     duck.com      public
4599     duck.com      public


In [67]:
# ✅ Исправляем домены, которые должны быть `corporate`
wrong_public = [
    "seturon.io", "3f.lu", "pagefly.io", "profiletree.com", "motionisme.com",
    "bayareapodcast.studio", "consultant.com", "viralchilly.com",
    "unityenergetics.org", "prodigy.net.mx"
]

df_merged_updated_2.loc[df_merged_updated_2['domain'].isin(wrong_public), "domain_type"] = "corporate"

print("✅ Ошибки исправлены: домены переведены в `corporate`")

✅ Ошибки исправлены: домены переведены в `corporate`


In [68]:
print(df_merged_updated_2[df_merged_updated_2['domain'].isin(wrong_public)][['domain', 'domain_type']])

                     domain domain_type
8                     3f.lu   corporate
12               seturon.io   corporate
396              seturon.io   corporate
402              seturon.io   corporate
408              seturon.io   corporate
409              seturon.io   corporate
419              seturon.io   corporate
420              seturon.io   corporate
441              seturon.io   corporate
442              seturon.io   corporate
454              seturon.io   corporate
466              seturon.io   corporate
483              seturon.io   corporate
505              seturon.io   corporate
506              seturon.io   corporate
510              seturon.io   corporate
517              seturon.io   corporate
524              seturon.io   corporate
525              seturon.io   corporate
526              seturon.io   corporate
527              seturon.io   corporate
528              seturon.io   corporate
529              seturon.io   corporate
533              seturon.io   corporate


In [86]:
import time

# ✅ Фильтруем только `corporate` домены
corporate_domains = df_merged_updated_2[df_merged_updated_2['domain_type'] == 'corporate'].copy()

print(f"🚀 Начинаем обработку {len(corporate_domains)} corporate-доменов...")

for index, row in corporate_domains.iterrows():
    try:
        domain = row['domain']
        print(f"🔹 Запрашиваем у API: {domain}")

        # ✅ Вызываем API для одной строки
        sector, company_country = classify_company_and_country(domain)

        # ✅ Записываем результат в основной DataFrame
        df_merged_updated_2.at[index, 'sector'] = sector
        df_merged_updated_2.at[index, 'company_country'] = company_country

        # ✅ Логируем результат
        print(f"✅ API ответил: {sector} - {company_country}")

    except Exception as e:
        print(f"❌ Ошибка API для {domain}: {e}")

print("✅ Обработка завершена!")

🚀 Начинаем обработку 728 corporate-доменов...
🔹 Запрашиваем у API: orbita.vc
✅ API ответил: Venture Capital - unknown
🔹 Запрашиваем у API: 3f.lu
✅ API ответил: Unknown - Luxembourg
🔹 Запрашиваем у API: seturon.io
✅ API ответил: Technology - United States
🔹 Запрашиваем у API: zentrapreneur.com
✅ API ответил: Unknown - Unknown
🔹 Запрашиваем у API: upthrust.eu
✅ API ответил: Technology - European Union
🔹 Запрашиваем у API: keeprise.ru
✅ API ответил: IT - Russia
🔹 Запрашиваем у API: mostfund.vc
✅ API ответил: Finance - United States
🔹 Запрашиваем у API: colegiosantamaria.edu.mx
✅ API ответил: Education - Mexico
🔹 Запрашиваем у API: oasisdemaadi.com
✅ API ответил: Unknown - Unknown
🔹 Запрашиваем у API: goodnoze.co.nz
✅ API ответил: Technology - New Zealand
🔹 Запрашиваем у API: netsetsoftware.com
✅ API ответил: Technology - United States
🔹 Запрашиваем у API: skiff.com
✅ API ответил: Technology - United States
🔹 Запрашиваем у API: pismo.ai
✅ API ответил: Technology - United States
🔹 Запрашива

In [87]:
import pandas as pd

# ✅ Фильтруем только `corporate` домены с Unknown или NaN в sector
unknown_sector = df_merged_updated_2[
    (df_merged_updated_2['domain_type'] == 'corporate') &
    (df_merged_updated_2['sector'].isna() | (df_merged_updated_2['sector'] == 'Unknown'))
]

# ✅ Фильтруем только `corporate` домены с Unknown или NaN в company_country
unknown_country = df_merged_updated_2[
    (df_merged_updated_2['domain_type'] == 'corporate') &
    (df_merged_updated_2['company_country'].isna() | (df_merged_updated_2['company_country'] == 'Unknown'))
]

# ✅ Уникальные домены для тех, у кого Unknown/NaN в sector
unique_unknown_sector = unknown_sector['domain'].unique()

# ✅ Уникальные домены для тех, у кого Unknown/NaN в company_country
unique_unknown_country = unknown_country['domain'].unique()

# ✅ Выводим результаты
print("📌 Уникальные домены с Unknown сектором:")
print(", ".join(unique_unknown_sector))

print("\n🌍 Уникальные домены с Unknown страной:")
print(", ".join(unique_unknown_country))

📌 Уникальные домены с Unknown сектором:
3f.lu, zentrapreneur.com, oasisdemaadi.com, wilscott.co.za, acname.com, luxtoday.lu, annardltd.com, projekt-interim.ch, yanaindustries.com, abplf.com, joeroc.com, safety-world.net, trotmaster.com, capstoneuae.com, lrpartnership.co.uk, mrggroup.ae, menschenundwege.de, paced.email, trumanpublishing.com, schillevoort.nl, philkurth.com.au, frysteen.com.au, benefitsonus.com, cetnob.com, bestglobaltrader.com, petramadisa.com, alexorlocal.com, royalassistants.com, michael-maurer.ch, shafra.com, lawirby.com, stonetree-group.com, comp-office.com, quellnatura.de, prs-resourcing.com, audiovibes-studios, azmediaproduction.com, businessbonheur.com, stproducties.nl, guinness.org.uk, campbellslife.com, waalt43.com, genesiprotection.com, mbnyservices.com, mccarty-consulting, scarmardo.com, miagd.com, insaalbers.de, myltd.link, bwl-berater.de, onlinebizdirect.com, eleinternacional.com, parlezentouteconfiance.com, canopusadvisors.com, ross-sivertsen.com, familylin

In [136]:
# ✅ Задаём API-ключи как переменные (НЕ хардкодим в коде)
HUNTER_API_KEY = "9d4f613429e9c347cb1153b2f3a3a05c08b24b12"
APOLLO_API_KEY = "I4DyPbAaIykeLrBi88FPCg"

# ✅ Проверка, что API-ключи заданы (не печатаем ключи!)
if not HUBSPOT_API_KEY or not HUNTER_API_KEY:
    raise ValueError("❌ API-ключи не установлены!")

In [137]:
print("✅ API-ключи загружены:", bool(HUBSPOT_API_KEY), bool(HUNTER_API_KEY))

✅ API-ключи загружены: True True


In [138]:
# Сохраняем API-ключи в переменные (замени YOUR_API_KEY на свои ключи)
GOOGLE_API_KEY = "твой апи"
WHOIS_API_KEY = "твой апи"

# Проверяем, что ключи сохранены
print(f"✅ API-ключ Google загружен: {bool(GOOGLE_API_KEY)}")
print(f"✅ API-ключ WHOIS загружен: {bool(WHOIS_API_KEY)}")

✅ API-ключ Google загружен: True
✅ API-ключ WHOIS загружен: True


In [160]:
# ✅ Уникальные домены (Unknown сектор ИЛИ Unknown страна)
unknown_domains = set([
    "3f.lu", "zentrapreneur.com", "oasisdemaadi.com", "wilscott.co.za", "acname.com",
    "luxtoday.lu", "annardltd.com", "projekt-interim.ch", "yanaindustries.com", "abplf.com",
    "joeroc.com", "safety-world.net", "trotmaster.com", "capstoneuae.com", "lrpartnership.co.uk",
    "mrggroup.ae", "menschenundwege.de", "paced.email", "trumanpublishing.com", "schillevoort.nl",
    "philkurth.com.au", "frysteen.com.au", "benefitsonus.com", "cetnob.com", "bestglobaltrader.com",
    "petramadisa.com", "alexorlocal.com", "royalassistants.com", "michael-maurer.ch", "shafra.com",
    "lawirby.com", "stonetree-group.com", "comp-office.com", "quellnatura.de", "prs-resourcing.com",
    "audiovibes-studios", "azmediaproduction.com", "businessbonheur.com", "stproducties.nl",
    "guinness.org.uk", "campbellslife.com", "waalt43.com", "genesiprotection.com", "mbnyservices.com",
    "mccarty-consulting", "scarmardo.com", "miagd.com", "insaalbers.de", "myltd.link", "bwl-berater.de",
    "onlinebizdirect.com", "eleinternacional.com", "parlezentouteconfiance.com", "canopusadvisors.com",
    "ross-sivertsen.com", "familylinksconsulting.com", "wes-productions.com", "annalerecords.com",
    "studiopiccinotti.it", "humanrace.com.au", "employeh.ca", "ecopetbox.com", "oddball.studio",
    "groogruxcreative.com", "hannesreick.de", "wsypc.com", "frankforward.nl", "eskk.co.uk",
    "saylesindustries.com", "schweller.com", "mdbsllc.com", "eugenklaus.de", "fun-promotion.gr",
    "authorsonmission.com", "btrcompanies.com", "scoot.llc", "mcttrainingconsultant.com", "apmz.net",
    "magnoliamatters.com", "dbje.de", "nofootprintgroup.com", "ruhtan.com", "9rok.com.au",
    "jkce.de", "aspriano.com", "ddincmail.org", "krk-group.com", "kim-ao.com", "gesforma.com",
    "xsk-m.com", "ylmconnect.org", "levenue.com", "crinali.it", "accordglobaltrade.com",
    "kramertrading.de", "hasaw.lu", "fishinnovationgroup.com", "drbuehne.com", "bawsny.com",
    "paullange.com.au", "consultant.com", "rte199.com", "thejensenteam.ca", "greenfamily.biz",
    "jcnorris.com", "shinebox.ca", "eabuck.com"
])

# ✅ Создаём словарь с Unknown значениями
cached_results = {domain: ("Unknown", "Unknown") for domain in unknown_domains}

# ✅ Выводим количество доменов для обработки
print(f"📌 Всего доменов в `cached_results`: {len(cached_results)}")

📌 Всего доменов в `cached_results`: 107


In [158]:
import requests
import json

# ✅ Функция для обработки страны (приведение к единому формату)
def clean_country(country, domain):
    country = country.strip().title()
    
    # Приводим к единому формату "United States"
    if country in ["Usa", "United States", "U.S.", "America", "North America"]:
        return "United States"
    
    # Если OpenAI вернул "Europe", "Asia", "North America" – пробуем уточнить по домену
    if country in ["Europe", "Asia", "North America"]:
        domain_extension = domain.split(".")[-1]
        domain_country_map = {
            "gr": "Greece",
            "lu": "Luxembourg",
            "de": "Germany",
            "fr": "France",
            "it": "Italy",
            "es": "Spain",
            "nl": "Netherlands",
            "se": "Sweden",
            "uk": "United Kingdom",
            "jp": "Japan",
            "ru": "Russia",
            "in": "India",
            "cn": "China",
            "br": "Brazil",
            "ca": "Canada"
        }
        return domain_country_map.get(domain_extension, country)  # Если не нашли в мапе, оставляем как есть

    return country

# ✅ Функция для приведения сегмента к нормальному формату
def clean_segment(segment):
    return segment.strip().capitalize()  # Первая буква заглавная, остальные маленькие

# ✅ Функция для получения страны из WHOIS API
def get_whois_country(domain):
    url = f"https://www.whoisxmlapi.com/whoisserver/WhoisService?apiKey={WHOIS_API_KEY}&domainName={domain}&outputFormat=json"
    try:
        response = requests.get(url)
        data = response.json()
        country = data.get("WhoisRecord", {}).get("registrant", {}).get("country", "Unknown")
        return country if country else "Unknown"
    except Exception as e:
        print(f"⚠️ Ошибка WHOIS API для {domain}: {e}")
        return "Unknown"

# ✅ Функция для получения сегмента через OpenAI API (улучшенная версия)
def get_openai_info(domain, retry=False):
    try:
        print(f"🔍 Запрос в OpenAI API для {domain}...")
        prompt = f"""
Определи страну и сегмент по полному домену {domain}. 
Ответь JSON с ключами 'country' и 'segment'. 

🎯 **Требования к ответу:**  
1️⃣ **Страна должна быть точной** ('United States', 'Greece', 'Luxembourg', 'Japan').  
   - Учитывай **TLD (расширение, например, .gr = Greece, .jp = Japan)**.  
   - Также анализируй **субдомен** (`gov.ru` → Russia, `co.uk` → United Kingdom, `edu.cn` → China).  
   - ❌ **Не используй "Europe", "Asia", "North America"** — всегда давай конкретную страну.  

2️⃣ **Сегмент должен быть детализированным**  
   - Например: 'Luxury hotel chain', 'Equestrian betting platform', 'Cybersecurity solutions', 'Streaming service'.  
   - ❌ **Не используй**: 'Business', 'Corporation', 'Thing', 'Organization', 'Website', 'Digital marketing agency'.  

Если сегмент не ясен, попробуй определить его по косвенным признакам.
"""
        if retry:
            prompt += " 🔁 Второй запрос: уточни категорию еще точнее." 

        response = client.chat.completions.create(
            model="gpt-4-turbo",
            messages=[{"role": "user", "content": prompt}]
        )

        if not response or not response.choices or not response.choices[0].message.content:
            print(f"⚠️ Пустой ответ от OpenAI API для {domain}")
            return "Unknown", "Not found"

        raw_content = response.choices[0].message.content.strip("```json").strip("```").strip()

        try:
            response_json = json.loads(raw_content)
            country = response_json.get("country", "Unknown")
            segment = response_json.get("segment", "Not found")

            # 🔥 Повторный запрос, если сегмент слишком общий
            if segment in ["Thing", "Organization", "Corporation", "Website", "Digital marketing agency"] and not retry:
                print(f"⚠️ Повторный запрос к OpenAI API для уточнения сегмента {domain}")
                return get_openai_info(domain, retry=True)

            return country, segment
        except json.JSONDecodeError as e:
            print(f"⚠️ Ошибка парсинга JSON OpenAI API для {domain}: {raw_content} ({e})")
            return "Unknown", "Not found"

    except Exception as e:
        print(f"⚠️ Ошибка OpenAI API для {domain}: {e}")
        return "Unknown", "Not found"

# ✅ Основная функция обработки домена
def get_domain_info(domain):
    print(f"🚀 Обрабатываем {domain}...")

    # 1️⃣ Получаем страну через WHOIS
    country = get_whois_country(domain)

    # 2️⃣ Если страна не найдена, пробуем OpenAI API
    if country == "Unknown":
        openai_country, _ = get_openai_info(domain)
        if openai_country not in ["Unknown", "Global", "Europe", "Asia", "North America"]:
            country = openai_country

    # 3️⃣ Приводим страну к единому формату (проверяем домен и префикс)
    country = clean_country(country, domain)

    # 4️⃣ Пробуем получить сегмент через OpenAI
    _, segment = get_openai_info(domain)

    # 5️⃣ Приводим сегмент к правильному формату
    segment = clean_segment(segment)

    return domain, country, segment

# ✅ Тестируем на 10 доменах
test_domains = [
    "google.com", "microsoft.com", "amazon.com", "adidas.com",
    "fun-promotion.gr", "luxtoday.lu", "stonetree-group.com",
    "trotmaster.com", "ruhtan.com", "oddball.studio",
    "news.bbc.co.uk", "shop.rakuten.co.jp", "gov.ru", "edu.cn"
]

results = [get_domain_info(domain) for domain in test_domains]

# ✅ Вывод результатов
df_results = pd.DataFrame(results, columns=["domain", "country", "segment"])
print(df_results)

🚀 Обрабатываем google.com...
🔍 Запрос в OpenAI API для google.com...
🚀 Обрабатываем microsoft.com...
🔍 Запрос в OpenAI API для microsoft.com...
🚀 Обрабатываем amazon.com...
🔍 Запрос в OpenAI API для amazon.com...
🚀 Обрабатываем adidas.com...
🔍 Запрос в OpenAI API для adidas.com...
🚀 Обрабатываем fun-promotion.gr...
🔍 Запрос в OpenAI API для fun-promotion.gr...
🔍 Запрос в OpenAI API для fun-promotion.gr...
🚀 Обрабатываем luxtoday.lu...
🔍 Запрос в OpenAI API для luxtoday.lu...
🔍 Запрос в OpenAI API для luxtoday.lu...
🚀 Обрабатываем stonetree-group.com...
🔍 Запрос в OpenAI API для stonetree-group.com...
🚀 Обрабатываем trotmaster.com...
🔍 Запрос в OpenAI API для trotmaster.com...
🔍 Запрос в OpenAI API для trotmaster.com...
🚀 Обрабатываем ruhtan.com...
🔍 Запрос в OpenAI API для ruhtan.com...
🚀 Обрабатываем oddball.studio...
🔍 Запрос в OpenAI API для oddball.studio...
🔍 Запрос в OpenAI API для oddball.studio...
🚀 Обрабатываем news.bbc.co.uk...
🔍 Запрос в OpenAI API для news.bbc.co.uk...
🔍 За

In [161]:
# ✅ Обновляем словарь cached_results новыми странами и сегментами
for domain in unknown_domains:
    country, segment = get_openai_info(domain)  # Получаем страну и сегмент
    country = clean_country(country, domain)  # Приводим страну к единому формату
    segment = clean_segment(segment)  # Приводим сегмент к стандартному виду

    cached_results[domain] = (country, segment)  # Обновляем в формате {домен: (страна, сегмент)}

# ✅ Выводим обновленный словарь
print(f"📌 Обновлено {len(cached_results)} доменов")
print(json.dumps(cached_results, indent=4))  # Красиво печатаем JSON

🔍 Запрос в OpenAI API для schweller.com...
🔍 Запрос в OpenAI API для menschenundwege.de...
🔍 Запрос в OpenAI API для wilscott.co.za...
🔍 Запрос в OpenAI API для gesforma.com...
🔍 Запрос в OpenAI API для magnoliamatters.com...
🔍 Запрос в OpenAI API для bawsny.com...
🔍 Запрос в OpenAI API для mdbsllc.com...
🔍 Запрос в OpenAI API для jkce.de...
🔍 Запрос в OpenAI API для myltd.link...
🔍 Запрос в OpenAI API для scarmardo.com...
🔍 Запрос в OpenAI API для hannesreick.de...
🔍 Запрос в OpenAI API для 9rok.com.au...
🔍 Запрос в OpenAI API для stproducties.nl...
🔍 Запрос в OpenAI API для shinebox.ca...
🔍 Запрос в OpenAI API для xsk-m.com...
⚠️ Ошибка парсинга JSON OpenAI API для xsk-m.com: {
  "country": "United States",
  "segment": "Generic corporate or personal website"
}
```

**Обоснование решения:**
1. TLD `.com` используется международно и не указывает на конкретную страну. Однако, поскольку `.com` первоначально ассоциировался с "commercial" и чаще всего используется в США, можно предположит

In [162]:
from collections import Counter

# ✅ Подсчет уникальных стран и их количества
country_counts = Counter(country for country, segment in cached_results.values())

# ✅ Подсчет уникальных сегментов и их количества
segment_counts = Counter(segment for country, segment in cached_results.values())

# ✅ Вывод результатов
country_counts, segment_counts

(Counter({'United States': 56,
          'Germany': 9,
          'Australia': 5,
          'Unknown': 5,
          'International': 3,
          'Netherlands': 3,
          'Canada': 3,
          'United Kingdom': 3,
          'Luxembourg': 3,
          'Switzerland': 2,
          'United Arab Emirates': 2,
          'Italy': 2,
          'South Africa': 1,
          'Greece': 1,
          'Commercial (International)': 1,
          'Commercial': 1,
          'Belize': 1,
          'Oman': 1,
          'Commercial (Generic)': 1,
          'France': 1,
          'Comoros': 1,
          'Generic': 1,
          'Angola': 1}),
 Counter({'Unknown': 18,
          'Not found': 5,
          'Personal website': 3,
          'Limited liability company': 2,
          'Business consulting services': 2,
          'Automotive parts manufacturer': 1,
          'German language website': 1,
          'General business entity': 1,
          'Professional training and coaching platform': 1,
          'En

In [165]:
cached_results.update({
    # ✅ Ручные исправления найденных доменов
    "bawsny.com": ("Test", "Test"),
    "xsk-m.com": ("Test", "Test"),
    "jcnorris.com": ("Test", "Test"),
    "cetnob.com": ("Test", "Test"),

    "frankforward.nl": ("Netherlands", "Marketing & Communication"),
    "eabuck.com": ("United States", "Financial services"),
    "drbuehne.com": ("Germany", "Enterprise IT architecture"),
    "ylmconnect.org": ("United States", "Religious organization"),
    "alexorlocal.com": ("United States", "Marketing agency"),

    # ✅ Дополнительные исправления (из прошлых шагов)
    "rte199.com": ("Canada", "Clothing & fashion brand"),
    "yanaindustries.com": ("Malaysia", "Interior decorators"),
    "wsypc.com": ("Philippines", "Online electronics store"),
    "joeroc.com": ("Canada", "Music production"),
    "abplf.com": ("Saudi Arabia", "Legal services"),
    
    # ✅ Исправление домена (Dr. Bühne)
    "drbuehne.me": cached_results.pop("drbuehne.com")
})

In [168]:
cached_results.update({
    # ✅ Конкретные исправления по твоим указаниям
    "jkce.de": ("Germany", "IT"),
    "myltd.link": ("Test", "Test"),
    "eskk.co.uk": ("United Kingdom", "Martial Arts & Fitness"),
    "insaalbers.de": ("Germany", "Art"),
    "dbje.de": ("Germany", "Digital Branding & Marketing"),
    "employeh.ca": ("Canada", "HR & Recruitment"),
    "lrpartnership.co.uk": ("United Kingdom", "Event Management"),
    "3f.lu": ("Luxembourg", "IT Startup"),
    "hasaw.lu": ("Luxembourg", "Occupational Safety & Security"),
    "frysteen.com.au": ("Australia", "Photo Studio"),
    "eleinternacional.com": ("Spain", "Professional Training & Education"),
    "waalt43.com": ("Test", "Test"),
    "crinali.it": ("Italy", "Well-being, Sustainability, Tourism, Health"),
    "schillevoort.nl": ("Netherlands", "Healthcare"),
    "paced.email": ("Test", "Test"),
    "kim-ao.com": ("Test", "Test"),
    "drbuehne.me": ("Germany", "Digital Strategy & Technological Innovation")
})

In [169]:
# ✅ Фильтруем домены с нерелевантными значениями
irrelevant_countries = {"Unknown", "International", "Commercial (International)", "Commercial", "Commercial (Generic)"}
irrelevant_segments = {"Unknown", "Not found", "Unknown specific segment", "Generic", "Unspecified"}

# ✅ Список доменов с нерелевантными значениями
irrelevant_domains = {domain: (country, segment) for domain, (country, segment) in cached_results.items() 
                      if country in irrelevant_countries or segment in irrelevant_segments}

# ✅ Вывод результата
irrelevant_domains

{}

In [170]:
# ✅ Фильтруем домены с "Unknown", "Not found", "Unknown specific segment"
problematic_segments = {domain: (country, segment) for domain, (country, segment) in cached_results.items()
                        if segment in {"Unknown", "Not found", "Unknown specific segment"}}

# ✅ Выводим список проблемных сегментов
problematic_segments

{}

In [187]:
from collections import Counter

# ✅ Собираем списки стран и сегментов
unique_countries = Counter(country for country, _ in cached_results.values())
unique_segments = Counter(segment for _, segment in cached_results.values())

# ✅ Выводим уникальные страны и их количество
unique_countries, unique_segments

(Counter({'United States': 54,
          'Germany': 10,
          'Test': 8,
          'Australia': 5,
          'Canada': 5,
          'Netherlands': 3,
          'United Kingdom': 3,
          'Luxembourg': 3,
          'Switzerland': 2,
          'United Arab Emirates': 2,
          'Italy': 2,
          'South Africa': 1,
          'Greece': 1,
          'Malaysia': 1,
          'Belize': 1,
          'Oman': 1,
          'Philippines': 1,
          'Spain': 1,
          'France': 1,
          'Saudi Arabia': 1,
          'Comoros': 1}),
 Counter({'Finance & Investment': 22,
          'Media & Entertainment': 16,
          'Retail & Food': 13,
          'Test': 8,
          'Technology': 8,
          'Education': 6,
          'Marketing': 6,
          'Human Resources': 6,
          'Government & Public Sector': 3,
          'Sports': 2,
          'Real Estate': 2,
          'Manufacturing & Chemicals': 2,
          'Fashion': 2,
          'Construction': 2,
          'Travel & Hos

In [172]:
df_merged_updated_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 21 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [175]:
df_merged_updated_2["sector"] = df_merged_updated_2["sector"].replace({
    "Legal": "Legal Services",
    "IT": "Technology",
    "Healthcare": "Healthcare & Insurance",
    "Insurance": "Healthcare & Insurance",
    "Entertainment": "Media & Entertainment",
    "Media": "Media & Entertainment",
    "Public Sector": "Government & Public Sector",
    "Government": "Government & Public Sector",
    "Hospitality": "Travel & Hospitality",
    "Travel": "Travel & Hospitality",
    "HR": "Human Resources",
    "Recruitment": "Human Resources",
    "Food & Beverage": "Retail & Food",
    "Retail": "Retail & Food",
    "Chemicals": "Manufacturing & Chemicals",
    "Manufacturing": "Manufacturing & Chemicals",
    "Finance": "Finance & Investment",
    "Venture Capital": "Finance & Investment"
})

In [185]:
df_merged_updated_2['sector'].unique()

array([None, 'Finance & Investment', 'Unknown', 'Technology', 'Education',
       'Automotive', 'Travel & Hospitality', 'Healthcare & Insurance',
       'Marketing', 'Government & Public Sector', 'Beauty', 'unknown',
       'Media & Entertainment', 'Legal Services', 'Real Estate',
       'Retail & Food', 'Fashion', 'Manufacturing & Chemicals',
       'Human Resources', 'Sports', 'Construction', 'Energy'],
      dtype=object)

In [179]:
sector_mapping = {
    "Finance & Investment": [
        "Financial advisory services", "Financial services",
        "Investment firm", "Corporate services", "Banking"
    ],
    "Technology": [
        "IT", "Software development", "Digital Strategy & Technological Innovation",
        "Information technology services", "Cybersecurity solutions",
        "Enterprise IT architecture", "IT Startup", "Online business directory"
    ],
    "Education": [
        "Professional Training & Education", "Educational platform for spanish language",
        "Training and consulting services", "Confidence building platform"
    ],
    "Automotive": [
        "Automotive parts manufacturer"
    ],
    "Travel & Hospitality": [
        "Tourism", "Travel agency", "Online lifestyle or luxury magazine"
    ],
    "Healthcare & Insurance": [
        "Healthcare", "Medical services", "Human resources consulting"
    ],
    "Marketing": [
        "Marketing agency", "Marketing & Communication",
        "Digital marketing services", "Advertising", "Promotional activities"
    ],
    "Government & Public Sector": [
        "Non-profit organization", "Government services", "Religious organization"
    ],
    "Beauty": [
        "Skincare and beauty products"
    ],
    "Media & Entertainment": [
        "Music record label", "Music production", "Publishing company",
        "Media and entertainment productions", "Audio recording and production studio",
        "Media production company", "News broadcasting service"
    ],
    "Legal Services": [
        "Legal services", "Law firm"
    ],
    "Real Estate": [
        "Real estate team", "Property management"
    ],
    "Retail & Food": [
        "E-commerce platform", "Retail business", "Clothing & fashion brand",
        "Food & beverage", "Soup and food products company"
    ],
    "Fashion": [
        "Fashion industry", "Clothing & fashion brand"
    ],
    "Manufacturing & Chemicals": [
        "Manufacturing", "Chemical industry"
    ],
    "Human Resources": [
        "HR & Recruitment", "Employment agency"
    ],
    "Sports": [
        "Martial Arts & Fitness", "Equestrian betting platform", "Athletic apparel and footwear"
    ],
    "Construction": [
        "Construction company", "Safety and security solutions",
        "Occupational Safety & Security"
    ],
    "Energy": [
        "Renewable energy", "Oil & gas", "Energy solutions"
    ]
}

def map_to_existing_sector(segment):
    for sector, keywords in sector_mapping.items():
        if segment in keywords:
            return sector
    return "General business"  # Если нет точного совпадения, ставим общее

# ✅ Обновляем `cached_results` с учетом маппинга
for domain, (country, segment) in cached_results.items():
    cached_results[domain] = (country, map_to_existing_sector(segment))

In [181]:
sector_mapping = {
    "Finance & Investment": [
        "Financial advisory services", "Financial services",
        "Investment firm", "Corporate services", "Banking"
    ],
    "Technology": [
        "IT", "Software development", "Digital Strategy & Technological Innovation",
        "Information technology services", "Cybersecurity solutions",
        "Enterprise IT architecture", "IT Startup", "Online electronics store"
    ],
    "Education": [
        "Professional Training & Education", "Educational platform for spanish language",
        "Training and consulting services", "Confidence building platform"
    ],
    "Automotive": [
        "Automotive parts manufacturer"
    ],
    "Travel & Hospitality": [
        "Tourism", "Travel agency", "Online lifestyle or luxury magazine",
        "Real estate team"
    ],
    "Healthcare & Insurance": [
        "Healthcare", "Medical services", "Human resources consulting"
    ],
    "Marketing": [
        "Marketing agency", "Marketing & Communication",
        "Digital marketing services", "Advertising", "Promotional activities"
    ],
    "Government & Public Sector": [
        "Non-profit organization", "Government services", "Religious organization"
    ],
    "Beauty": [
        "Skincare and beauty products"
    ],
    "Media & Entertainment": [
        "Music record label", "Music production", "Publishing company",
        "Media and entertainment productions", "Audio recording and production studio",
        "Media production company", "News broadcasting service"
    ],
    "Legal Services": [
        "Legal services", "Law firm"
    ],
    "Real Estate": [
        "Property management"
    ],
    "Retail & Food": [
        "E-commerce platform", "Retail business", "Clothing & fashion brand",
        "Food & beverage", "Soup and food products company"
    ],
    "Fashion": [
        "Fashion industry", "Clothing & fashion brand"
    ],
    "Manufacturing & Chemicals": [
        "Manufacturing", "Chemical industry"
    ],
    "Human Resources": [
        "HR & Recruitment", "Employment agency"
    ],
    "Sports": [
        "Martial Arts & Fitness", "Equestrian betting platform", "Athletic apparel and footwear"
    ],
    "Construction": [
        "Construction company", "Safety and security solutions",
        "Occupational Safety & Security"
    ],
    "Energy": [
        "Renewable energy", "Oil & gas", "Energy solutions"
    ]
}


def map_to_existing_sector(segment):
    for sector, keywords in sector_mapping.items():
        if segment in keywords:
            return sector
    return "unknown"  # Если не попадает в список, ставим "unknown"

# ✅ Обновляем `cached_results` с учетом маппинга
for domain, (country, segment) in cached_results.items():
    cached_results[domain] = (country, map_to_existing_sector(segment))

In [186]:
# 🔥 Восстанавливаю кешированные результаты с последней рабочей версии

cached_results = {
    "schweller.com": ("United States", "Automotive"),
    "menschenundwege.de": ("Germany", "Education"),
    "wilscott.co.za": ("South Africa", "Finance & Investment"),
    "gesforma.com": ("United States", "Education"),
    "magnoliamatters.com": ("United States", "Government & Public Sector"),
    "bawsny.com": ("Test", "Test"),
    "mdbsllc.com": ("United States", "Finance & Investment"),
    "jkce.de": ("Germany", "Technology"),
    "myltd.link": ("Test", "Test"),
    "scarmardo.com": ("United States", "Retail & Food"),
    "hannesreick.de": ("Germany", "Media & Entertainment"),
    "9rok.com.au": ("Australia", "Retail & Food"),
    "stproducties.nl": ("Netherlands", "Media & Entertainment"),
    "shinebox.ca": ("Canada", "Retail & Food"),
    "xsk-m.com": ("Test", "Test"),
    "comp-office.com": ("United States", "Retail & Food"),
    "philkurth.com.au": ("Australia", "Media & Entertainment"),
    "fun-promotion.gr": ("Greece", "Marketing"),
    "ross-sivertsen.com": ("United States", "Media & Entertainment"),
    "eskk.co.uk": ("United Kingdom", "Sports"),
    "jcnorris.com": ("Test", "Test"),
    "consultant.com": ("United States", "Finance & Investment"),
    "aspriano.com": ("United States", "Retail & Food"),
    "oasisdemaadi.com": ("United States", "Real Estate"),
    "familylinksconsulting.com": ("United States", "Human Resources"),
    "insaalbers.de": ("Germany", "Art"),
    "canopusadvisors.com": ("United States", "Finance & Investment"),
    "yanaindustries.com": ("Malaysia", "Manufacturing & Chemicals"),
    "eugenklaus.de": ("Germany", "Media & Entertainment"),
    "trotmaster.com": ("United States", "Sports"),
    "ddincmail.org": ("United States", "Education"),
    "frankforward.nl": ("Netherlands", "Marketing"),
    "cetnob.com": ("Test", "Test"),
    "eabuck.com": ("United States", "Finance & Investment"),
    "apmz.net": ("United States", "Technology"),
    "annardltd.com": ("United States", "Finance & Investment"),
    "saylesindustries.com": ("United States", "Marketing"),
    "dbje.de": ("Germany", "Marketing"),
    "royalassistants.com": ("United States", "Human Resources"),
    "employeh.ca": ("Canada", "Human Resources"),
    "joeroc.com": ("Canada", "Media & Entertainment"),
    "lrpartnership.co.uk": ("United Kingdom", "Event Management"),
    "projekt-interim.ch": ("Switzerland", "Human Resources"),
    "3f.lu": ("Luxembourg", "Technology"),
    "rte199.com": ("Canada", "Fashion"),
    "guinness.org.uk": ("United Kingdom", "Retail & Food"),
    "capstoneuae.com": ("United Arab Emirates", "Finance & Investment"),
    "btrcompanies.com": ("United States", "Finance & Investment"),
    "studiopiccinotti.it": ("Italy", "Media & Entertainment"),
    "trumanpublishing.com": ("United States", "Media & Entertainment"),
    "safety-world.net": ("United States", "Construction"),
    "wes-productions.com": ("United States", "Media & Entertainment"),
    "levenue.com": ("United States", "Travel & Hospitality"),
    "hasaw.lu": ("Luxembourg", "Construction"),
    "krk-group.com": ("United States", "Finance & Investment"),
    "greenfamily.biz": ("Belize", "Retail & Food"),
    "paullange.com.au": ("Australia", "Retail & Food"),
    "frysteen.com.au": ("Australia", "Media & Entertainment"),
    "miagd.com": ("United States", "Retail & Food"),
    "ruhtan.com": ("Oman", "Retail & Food"),
    "humanrace.com.au": ("Australia", "Fashion"),
    "thejensenteam.ca": ("Canada", "Real Estate"),
    "accordglobaltrade.com": ("United States", "Finance & Investment"),
    "wsypc.com": ("Philippines", "Retail & Food"),
    "shafra.com": ("United States", "Beauty"),
    "ylmconnect.org": ("United States", "Government & Public Sector"),
    "eleinternacional.com": ("Spain", "Education"),
    "annalerecords.com": ("United States", "Media & Entertainment"),
    "acname.com": ("United States", "Finance & Investment"),
    "mcttrainingconsultant.com": ("United States", "Education"),
    "mrggroup.ae": ("United Arab Emirates", "Finance & Investment"),
    "nofootprintgroup.com": ("United States", "Government & Public Sector"),
    "azmediaproduction.com": ("United States", "Media & Entertainment"),
    "mccarty-consulting": ("United States", "Finance & Investment"),
    "parlezentouteconfiance.com": ("France", "Education"),
    "abplf.com": ("Saudi Arabia", "Legal Services"),
    "waalt43.com": ("Test", "Test"),
    "campbellslife.com": ("United States", "Retail & Food"),
    "bestglobaltrader.com": ("United States", "Finance & Investment"),
    "authorsonmission.com": ("United States", "Media & Entertainment"),
    "ecopetbox.com": ("United States", "Retail & Food"),
    "fishinnovationgroup.com": ("United States", "Technology"),
    "audiovibes-studios": ("United States", "Media & Entertainment"),
    "alexorlocal.com": ("United States", "Marketing"),
    "bwl-berater.de": ("Germany", "Finance & Investment"),
    "crinali.it": ("Italy", "Travel & Hospitality"),
    "genesiprotection.com": ("United States", "Technology"),
    "lawirby.com": ("United States", "Legal Services"),
    "luxtoday.lu": ("Luxembourg", "Media & Entertainment"),
    "groogruxcreative.com": ("United States", "Marketing"),
    "petramadisa.com": ("Comoros", "Finance & Investment"),
    "stonetree-group.com": ("United States", "Finance & Investment"),
    "prs-resourcing.com": ("United States", "Human Resources"),
    "schillevoort.nl": ("Netherlands", "Healthcare & Insurance"),
    "oddball.studio": ("United States", "Media & Entertainment"),
    "paced.email": ("Test", "Test"),
    "onlinebizdirect.com": ("United States", "Technology"),
    "businessbonheur.com": ("United States", "Finance & Investment"),
    "michael-maurer.ch": ("Switzerland", "Finance & Investment"),
    "kim-ao.com": ("Test", "Test"),
    "mbnyservices.com": ("United States", "Finance & Investment"),
    "quellnatura.de": ("Germany", "Manufacturing & Chemicals"),
    "benefitsonus.com": ("United States", "Human Resources"),
    "scoot.llc": ("United States", "Technology"),
    "zentrapreneur.com": ("United States", "Finance & Investment"),
    "kramertrading.de": ("Germany", "Finance & Investment"),
    "drbuehne.me": ("Germany", "Technology")
}

# ✅ Все восстановлено. Проверяем длину (должно быть 107)
len(cached_results)

107

In [194]:
# ✅ Создаем копию, чтобы не потерять исходные данные
df_merged_updated_3 = df_merged_updated_2.copy()

# ✅ Функция для замены значений по домену
def update_values(row):
    domain = row["domain"]
    if domain in cached_results:
        country, sector = cached_results[domain]
        return pd.Series([country, sector])
    return pd.Series([row["company_country"], row["sector"]])  # Оставляем старые значения, если нет в словаре

# ✅ Применяем обновления
df_merged_updated_3[["company_country", "sector"]] = df_merged_updated_3.apply(update_values, axis=1)

# ✅ Выводим количество обновленных записей
updated_count = (df_merged_updated_3["company_country"] != df_merged_updated_2["company_country"]).sum() + \
                (df_merged_updated_3["sector"] != df_merged_updated_2["sector"]).sum()

print(f"📌 Обновлено записей: {updated_count}")

📌 Обновлено записей: 8622


In [192]:
# Фильтруем только те строки, где обновились значения из словаря
updated_rows = df_merged_updated_3[df_merged_updated_3['domain'].isin(cached_results.keys())]

# Считаем, сколько из них реально обновилось
print(f"📌 Фактически обновленных доменов: {len(updated_rows)}")

📌 Фактически обновленных доменов: 111


In [195]:
df_merged_updated_3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 21 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [198]:
# Вывод уникальных стран и их количество
unique_countries = df_merged_updated_3["company_country"].value_counts()

# Вывод уникальных секторов и их количество
unique_sectors = df_merged_updated_3["sector"].value_counts()

unique_sectors

sector
Technology                    448
Finance & Investment           49
Marketing                      37
Education                      35
Healthcare & Insurance         26
Media & Entertainment          26
Retail & Food                  18
unknown                        11
Real Estate                    10
Manufacturing & Chemicals       9
Test                            9
Human Resources                 8
Legal Services                  8
Government & Public Sector      8
Travel & Hospitality            6
Construction                    4
Automotive                      4
Sports                          3
Fashion                         3
Beauty                          2
Event Management                1
Art                             1
Unknown                         1
Energy                          1
Name: count, dtype: int64

In [203]:
unique_countries

company_country
United States           416
Germany                  46
Switzerland              30
unknown                  28
Australia                21
United Kingdom           20
Canada                   16
Italy                    16
Test                      9
Sweden                    8
India                     7
Netherlands               7
France                    6
Unknown                   6
Spain                     6
New Zealand               5
Luxembourg                5
Saudi Arabia              5
United Arab Emirates      5
Belgium                   5
Mexico                    4
Japan                     4
Vietnam                   3
Taiwan                    3
Ukraine                   3
Poland                    3
Denmark                   3
Israel                    3
Philippines               2
Czech Republic            2
Chile                     2
China                     2
Norway                    2
Turkey                    2
Austria                   2
Sout

In [201]:
updates = {
    "sfpmfoodconsulting.com": ("Canada", "Retail & Food"),
    "e.com": ("Germany", "Technology"),
    "demo.com": ("Test", "Test"),
    "goering.de": ("Germany", "Technology"),
    "rentadirector.africa": ("United Kingdom", "Finance & Investment"),
    "aschenberner-consult": ("Germany", "Technology"),
    "consilium-agilis": ("Germany", "Finance & Investment"),
    "drbuehne.com": ("Germany", "Technology"),
    "samvetedistribuciones.com": ("Mexico", "Retail & Food"),
    "mtedenvillagecentre.co.nz": ("New Zealand", "Government & Public Sector"),
    "msw-werbeagent": ("Germany", "Human Resources"),
    "urbfaulds.ca": ("Canada", "Healthcare & Insurance")
}

# ✅ Обновляем данные в df_merged_updated_3 по ключу 'domain'
df_merged_updated_3.loc[df_merged_updated_3['domain'].isin(updates.keys()), ['company_country', 'sector']] = \
    df_merged_updated_3['domain'].map(updates).apply(pd.Series)

In [205]:
# Словарь с обновленными значениями стран и секторов
updated_country_sector = {
    "orbita.vc": ("Luxembourg", "Technology"),
    "st.uew.edu": ("Ghana", "Education"),
    "akaisschool.com": ("United Arab Emirates", "Education"),
    "ltdmail.io": ("Test", "Test"),
    "ai-innovator.net": ("United States", "Technology"),
    "futureeducation.ai": ("India", "Education"),
    "resto.marketing": ("United States", "Marketing"),
    "gamesqlaw.com": ("United States", "Legal Services"),
    "0706.agency": ("United States", "Marketing"),
    "hearinghealthcarecentre.co": ("United Kingdom", "Healthcare & Insurance"),
    "algorithmicschool.com": ("Netherlands", "Education"),
    "iwantonlinemarketing.com": ("United States", "Marketing"),
    "yiulab.network": ("Germany", "Technology"),
    "kpifinancialcoaching": ("United States", "Finance & Investment"),
    "virtualix.ai": ("United States", "Technology"),
    "metal-forming.eu": ("Germany", "Manufacturing & Chemicals"),
    "apsilonhotels.com": ("United States", "Travel & Hospitality"),
    "santa-marketing.com": ("Belgium", "Marketing"),
    "oriens.consulting": ("Italy", "Government & Public Sector"),
    "dasilva.capital": ("United Kingdom", "Real Estate"),
    "infratechcivil.com": ("Canada", "Construction"),
    "leadsprout.marketing": ("United States", "Marketing"),
    "nbi.academy": ("Test", "Test")
}

# Обновляем значения в DataFrame
df_merged_updated_3['company_country'] = df_merged_updated_3.apply(
    lambda row: updated_country_sector[row['domain']][0] 
    if row['domain'] in updated_country_sector else row['company_country'], axis=1
)

df_merged_updated_3['sector'] = df_merged_updated_3.apply(
    lambda row: updated_country_sector[row['domain']][1] 
    if row['domain'] in updated_country_sector else row['sector'], axis=1
)

# Проверяем, сколько записей обновлено
updated_count = df_merged_updated_3[df_merged_updated_3['domain'].isin(updated_country_sector.keys())].shape[0]
print(f"📌 Обновлено записей: {updated_count}")


📌 Обновлено записей: 33


In [214]:
# Фильтруем данные по условиям
filtered_domains = df_merged_updated_3[
    (df_merged_updated_3["domain"].str.endswith(".com")) & 
    (df_merged_updated_3["company_country"] == "United States") & 
    (df_merged_updated_3["domain_type"] == "corporate") & 
    (df_merged_updated_3["sector"] == "Technology")
]

# Получаем уникальные значения и их количество
unique_domains = filtered_domains["domain"].nunique()
unique_countries = filtered_domains["company_country"].nunique()
unique_sectors = filtered_domains["sector"].nunique()

# Выводим результаты
print(f"📌 Уникальных доменов: {unique_domains}")
print(f"📌 Уникальных стран: {unique_countries}")
print(f"📌 Уникальных секторов: {unique_sectors}")

# Выводим сами уникальные значения
print("\n🌍 Уникальные домены:")
print(filtered_domains["domain"].unique())

print("\n🌍 Уникальные страны:")
print(filtered_domains["company_country"].unique())

print("\n📊 Уникальные сектора:")
print(filtered_domains["sector"].unique())

📌 Уникальных доменов: 195
📌 Уникальных стран: 1
📌 Уникальных секторов: 1

🌍 Уникальные домены:
['netsetsoftware.com' 'skiff.com' 'agaseo.com' 'eryod.com' 'kravify.com'
 'em2lab.com' 'buzblox.com' 'splunk.com' 'mac.com' 'luravell.com'
 'gate.com' 'egela.com' 'dalebig.com' 'doolk.com' 'devncie.com'
 'laravel.com' 'kinsef.com' 'cartep.com' 'pismo.com' 'magtecsolutions.com'
 'netsoil.com' 'patentsmarter.com' 'degcos.com' 'alterego.com'
 'expertslides.com' 'perfectlyimperfectdigital.com' 'clientamp.com'
 'okadrian.com' 'sitesset.com' 'betranslated.com'
 'provisionsinternational.com' 'navigist.com' 'desightstudio.com'
 'marchub.com' 'naastepad.com' 'rainmakercommerce.com' 'gobizup.com'
 'venturaix.com' 'creatorways.com' 'makopros.com' 'ncbhub.com' 'drvtx.com'
 'purplepuppyweb.com' 'tazlink.com' 'websting.com' 'sunflows.com'
 'certosa.com' 'datafanatics.com' 'txlholdings.com' 'halbertech.com'
 'solosyn.com' 'sousmedia.com' 'suyen.com' 'flashfilmmedia.com'
 'linked-sites.com' 'empowerize.com' 

In [267]:
# Создаем пустой словарь для повторной проверки 195 доменов
domains_to_recheck = {
    "netsetsoftware.com": None,
    "skiff.com": None,
    "agaseo.com": None,
    "eryod.com": None,
    "kravify.com": None,
    "em2lab.com": None,
    "buzblox.com": None,
    "splunk.com": None,
    "mac.com": None,
    "luravell.com": None,
    "gate.com": None,
    "egela.com": None,
    "dalebig.com": None,
    "doolk.com": None,
    "devncie.com": None,
    "laravel.com": None,
    "kinsef.com": None,
    "cartep.com": None,
    "pismo.com": None,
    "magtecsolutions.com": None,
    "netsoil.com": None,
    "patentsmarter.com": None,
    "degcos.com": None,
    "alterego.com": None,
    "expertslides.com": None,
    "perfectlyimperfectdigital.com": None,
    "clientamp.com": None,
    "okadrian.com": None,
    "sitesset.com": None,
    "betranslated.com": None,
    "provisionsinternational.com": None,
    "navigist.com": None,
    "desightstudio.com": None,
    "marchub.com": None,
    "naastepad.com": None,
    "rainmakercommerce.com": None,
    "gobizup.com": None,
    "venturaix.com": None,
    "creatorways.com": None,
    "makopros.com": None,
    "ncbhub.com": None,
    "drvtx.com": None,
    "purplepuppyweb.com": None,
    "tazlink.com": None,
    "websting.com": None,
    "sunflows.com": None,
    "certosa.com": None,
    "datafanatics.com": None,
    "txlholdings.com": None,
    "halbertech.com": None,
    "solosyn.com": None,
    "sousmedia.com": None,
    "suyen.com": None,
    "flashfilmmedia.com": None,
    "linked-sites.com": None,
    "empowerize.com": None,
    "redrammedia.com": None,
    "mastersts.com": None,
    "entechonline.com": None,
    "team-genius.com": None,
    "dralias.com": None,
    "solutions.com": None,
    "secure-otp.com": None,
    "nextstepwebdesign.com": None,
    "gimel.com": None,
    "passfwd.com": None,
    "techgrowthsolutions.com": None,
    "websmithian.com": None,
    "venturiteam.com": None,
    "ramtechpcs.com": None,
    "rinseart.com": None,
    "cellbris.com": None,
    "bonfirerevenue.com": None,
    "internetmediaproviders.com": None,
    "limitlessint.com": None,
    "igcadv.com": None,
    "indaco.com": None,
    "ispem.com": None,
    "leadtagger.com": None,
    "cpiprint.com": None,
    "onhires.com": None,
    "genesiprotection.com": None,
    "hraifi.com": None,
    "consultingfischer.com": None,
    "stoicera.com": None,
    "synergy-one.com": None,
    "avconnexions.com": None,
    "westimating.com": None,
    "odismanagement.com": None,
    "mztweb.com": None,
    "cloozo.com": None,
    "sourcingsegments.com": None,
    "onlinebizdirect.com": None,
    "rocketstarmedia.com": None,
    "dobulk.com": None,
    "asectra.com": None,
    "increasewebdesign.com": None,
    "visualtronics.com": None,
    "peachwoodlabs.com": None,
    "beaubrewerdigital.com": None,
    "machtailored.com": None,
    "gloknowles.com": None,
    "kirrontech.com": None,
    "vikingfinity.com": None,
    "absias.com": None,
    "jameagle.com": None,
    "adosnan.com": None,
    "kinayglobal.com": None,
    "maxinium.com": None,
    "trimonks.com": None,
    "sierraeeg.com": None,
    "nestvia.com": None,
    "natinnova.com": None,
    "digicybersec.com": None,
    "tapeditgo.com": None,
    "getrepr.com": None,
    "rqwd.com": None,
    "adeptgraphics.com": None,
    "acroins.com": None,
    "mytd.com": None,
    "intisarium.com": None,
    "ownitgroup.com": None,
    "sincoautomation.com": None,
    "operades.com": None,
    "getadroit.com": None,
    "bonfirerev.com": None,
    "3wh.com": None,
    "maxintegration.com": None,
    "cs.com": None,
    "pmoagility.com": None,
    "sharedteams.com": None,
    "cybrac.com": None,
    "bizzbeesolutions.com": None,
    "techacq.com": None,
    "xavadigital.com": None,
    "weeksoutstanding.com": None,
    "funkformat.com": None,
    "100-signals.com": None,
    "lightbolt.com": None,
    "incrementors.com": None,
    "freilink.com": None,
    "mkswebdesign.com": None,
    "contentleverage.com": None,
    "verycom.com": None,
    "robotalp.com": None,
    "novasu.com": None,
    "blackbird-digital.com": None,
    "mindsharedigital.com": None,
    "scopedesign.com": None,
    "iq310.com": None,
    "forezight.com": None,
    "new-fwd.com": None,
    "edectus.com": None,
    "dolasoft.com": None,
    "zengers.com": None,
    "consulta.com": None,
    "flagc.com": None,
    "thatleo.com": None,
    "doordash.com": None,
    "fishinnovationgroup.com": None,
    "psychray.com": None,
    "level365.com": None,
    "adminas.com": None,
    "quantumdigitalplus.com": None,
    "vadimatwork.com": None,
    "viralchilly.com": None,
    "somoseo.com": None,
    "extrainteger.com": None,
    "zadaoffice.com": None,
    "getmule.com": None,
    "motionisme.com": None,
    "ronete.com": None,
    "chosenx.com": None,
    "exdonuts.com": None,
    "mowline.com": None,
    "msssg.com": None,
    "cctoolz.com": None,
    "rabbitex.com": None,
    "curuth.com": None,
    "notipr.com": None,
    "peppydigital.com": None,
    "koolquest.com": None,
    "wegastudios.com": None,
    "embodee.com": None,
    "fhblack.com": None,
    "jensentek.com": None,
    "starlight-digital.com": None,
    "xposales.com": None,
    "neo.rr.com": None,
    "blancastella.com": None,
    "perfectiongroup.com": None,
    "excelitas.com": None,
    "itnnetworks.com": None,
    "accesstca.com": None,
    "mercurygate.com": None
}

# Проверяем количество доменов в словаре
len(domains_to_recheck)

195

In [310]:
import openai

# Указываем API-ключ
OPENAI_API_KEY = "твой апи"

# Создаём клиента OpenAI с API-ключом
client = openai.Client(api_key=OPENAI_API_KEY)

try:
    response = client.chat.completions.create(
        model="gpt-4",
        messages=[{"role": "user", "content": "Привет, тестируем API."}]
    )
    print("✅ OpenAI API работает корректно!")
    print(response)
except Exception as e:
    print(f"❌ Ошибка: {e}")

✅ OpenAI API работает корректно!
ChatCompletion(id='chatcmpl-B1JRJX0EQCIUz8EEu6qHsQVqUoYd2', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='Привет! Я готов помочь тебе провести тестирование API. У тебя есть конкретные вопросы или требования?', refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None))], created=1739652753, model='gpt-4-0613', object='chat.completion', service_tier='default', system_fingerprint=None, usage=CompletionUsage(completion_tokens=44, prompt_tokens=17, total_tokens=61, completion_tokens_details=CompletionTokensDetails(accepted_prediction_tokens=0, audio_tokens=0, reasoning_tokens=0, rejected_prediction_tokens=0), prompt_tokens_details=PromptTokensDetails(audio_tokens=0, cached_tokens=0)))


In [262]:
import requests

GOOGLE_API_KEY = "твой апи"
SEARCH_ENGINE_ID = "твой гугл айди"  # если у тебя есть кастомный поисковый движок

query = "netsetsoftware.com company industry country"
url = f"https://www.googleapis.com/customsearch/v1?q={query}&key={GOOGLE_API_KEY}&cx={SEARCH_ENGINE_ID}"

response = requests.get(url)
print(response.json())

{'kind': 'customsearch#search', 'url': {'type': 'application/json', 'template': 'https://www.googleapis.com/customsearch/v1?q={searchTerms}&num={count?}&start={startIndex?}&lr={language?}&safe={safe?}&cx={cx?}&sort={sort?}&filter={filter?}&gl={gl?}&cr={cr?}&googlehost={googleHost?}&c2coff={disableCnTwTranslation?}&hq={hq?}&hl={hl?}&siteSearch={siteSearch?}&siteSearchFilter={siteSearchFilter?}&exactTerms={exactTerms?}&excludeTerms={excludeTerms?}&linkSite={linkSite?}&orTerms={orTerms?}&dateRestrict={dateRestrict?}&lowRange={lowRange?}&highRange={highRange?}&searchType={searchType}&fileType={fileType?}&rights={rights?}&imgSize={imgSize?}&imgType={imgType?}&imgColorType={imgColorType?}&imgDominantColor={imgDominantColor?}&alt=json'}, 'queries': {'request': [{'title': 'Google Custom Search - netsetsoftware.com company industry country', 'totalResults': '654', 'searchTerms': 'netsetsoftware.com company industry country', 'count': 10, 'startIndex': 1, 'inputEncoding': 'utf8', 'outputEncoding

In [261]:
import requests

# 🔑 Вставь свой API-ключ Hunter
HUNTER_API_KEY = "твой апи"

def test_hunter_search(domain):
    url = f"https://api.hunter.io/v2/domain-search?domain={domain}&api_key={HUNTER_API_KEY}"
    
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    return f"Ошибка: {response.status_code}, {response.text}"

# Тест Hunter API
hunter_test_result = test_hunter_search("netsetsoftware.com")
print(hunter_test_result)


Ошибка: 429, {
  "errors": [
    {
      "id": "too_many_requests",
      "code": 429,
      "details": "You've reached the limit for the number of searches per billing period included in your plan."
    }
  ]
}


In [269]:
import requests

# 🔑 Вставь свой API-ключ Whois
WHOIS_API_KEY = "твой апи"

def test_whois_search(domain):
    url = f"https://www.whoisxmlapi.com/whoisserver/WhoisService?apiKey={WHOIS_API_KEY}&domainName={domain}&outputFormat=json"
    
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    return f"Ошибка: {response.status_code}, {response.text}"

# Тест Whois API
whois_test_result = test_whois_search("netsetsoftware.com")
print(whois_test_result)

{'WhoisRecord': {'createdDate': '2011-11-22T17:26:00.00Z', 'updatedDate': '2025-01-07T06:04:12.00Z', 'expiresDate': '2025-11-22T17:26:18.00Z', 'registrant': {'name': 'Whois Agent (566437353)', 'organization': 'Whois Privacy Protection Service, Inc.', 'street1': 'PO Box 639\nC/O netsetsoftware.com', 'city': 'Kirkland', 'state': 'WA', 'postalCode': '98083', 'country': 'UNITED STATES', 'countryCode': 'US', 'email': 'bfmydgjk@whoisprivacyprotect.com', 'telephone': '14252740657', 'fax': '14259744730', 'rawText': 'Registrant Name: Whois Agent (566437353)\nRegistrant Organization: Whois Privacy Protection Service, Inc.\nRegistrant Street: PO Box 639\nRegistrant Street: C/O netsetsoftware.com\nRegistrant City: Kirkland\nRegistrant State/Province: WA\nRegistrant Postal Code: 98083\nRegistrant Country: US\nRegistrant Phone: +1.4252740657\nRegistrant Fax: +1.4259744730\nRegistrant Email: bfmydgjk@whoisprivacyprotect.com'}, 'administrativeContact': {'name': 'Whois Agent', 'organization': 'Whois Pr

In [270]:
# === СПИСОК СПАМНЫХ КЛЮЧЕВЫХ СЛОВ ===
spam_keywords = [
    "temporary email", "disposable email", "email validation", 
    "abuse risk", "domain reputation", "spam", "fake", "blacklist"
]

# === ФУНКЦИЯ OpenAI API ===
def search_openai(domain, snippet):
    url = "https://api.openai.com/v1/chat/completions"
    headers = {"Authorization": f"Bearer {OPENAI_API_KEY}", "Content-Type": "application/json"}

    queries = {
        "country": f"Determine the country where the company associated with the domain '{domain}' operates. Additional context: {snippet}. Provide ONLY the country name. If the country is unknown, return 'Unknown'. Do not add explanations or additional text.",
        "company": f"Determine the exact name of the company (brand or legal name) associated with the domain '{domain}'. Additional context: {snippet}. Provide ONLY the company name. If the company is unknown, return 'Unknown'. Do not add explanations or additional text.",
        "sector": f"Determine the business sector of the company associated with the domain '{domain}'. Additional context: {snippet}. Provide ONLY the business sector (e.g., IT, Finance, Healthcare, etc.). If the sector is unknown, return 'Unknown'. Do not add explanations or additional text."
    }

    results = {}
    for key, query in queries.items():
        print(f"📡 Отправка в OpenAI для {domain} ({key})...")
        response = requests.post(url, json={"model": "gpt-4", "messages": [{"role": "user", "content": query}]}, headers=headers)

        if response.status_code == 200:
            try:
                result = response.json()["choices"][0]["message"]["content"].strip()
                if len(result.split()) > 5:  # Если ответ странный, повторяем запрос
                    print(f"⚠️ OpenAI дал странный ответ для {domain} ({key}), повторный запрос...")
                    return search_openai(domain, snippet)
                print(f"🟢 OpenAI нашел {key} для {domain}: {result}")
                results[key] = result
            except (KeyError, IndexError):
                print(f"🔴 OpenAI НЕ НАШЕЛ {key} для {domain}")
                results[key] = "Unknown"
        else:
            print(f"❌ Ошибка OpenAI API для {domain} ({key}): {response.status_code}")
            results[key] = "Unknown"

    return results

# === ФУНКЦИЯ Whois API ===
def search_whois(domain):
    url = f"https://www.whoisxmlapi.com/whoisserver/WhoisService?apiKey={WHOIS_API_KEY}&domainName={domain}&outputFormat=json"

    for attempt in range(2):  # Две попытки
        response = requests.get(url)
        if response.status_code == 200:
            try:
                data = response.json()
                country = data["WhoisRecord"]["registrant"].get("country")
                if country:
                    print(f"🟢 Whois нашел страну для {domain}: {country}")
                    return country
            except KeyError:
                print(f"🔴 Whois НЕ НАШЕЛ данных для {domain}")
                return "Unknown"
        print(f"❌ Ошибка Whois API для {domain}: {response.status_code} (Попытка {attempt + 1})")
        time.sleep(3)  # Ждем перед повторной попыткой

    return "Unknown"

# === СОХРАНЕНИЕ ВСЕХ ДОМЕНОВ В results ===
results = {}

for idx, domain in enumerate(domains_to_recheck.keys(), start=1):
    print(f"\n🔍 [{idx}/{len(domains_to_recheck)}] Запрос для {domain}...")

    company_name = None
    snippet = None
    whois_country = "Unknown"
    openai_data = {}

    # 1️⃣ Google API (если есть)
    google_data = search_google(domain)
    if google_data:
        company_name = google_data["company"]
        snippet = google_data["snippet"]

    # 2️⃣ Whois API
    whois_country = search_whois(domain)

    # 3️⃣ Проверяем, если нужно отправлять в OpenAI
    if whois_country == "UNITED STATES" or whois_country == "Unknown":
        if snippet and not any(spam in snippet.lower() for spam in spam_keywords):
            openai_data = search_openai(domain, snippet)

    # 4️⃣ Финальные данные
    final_country = openai_data.get("country", "Unknown") if openai_data.get("country") != "Unknown" else whois_country
    final_company = openai_data.get("company", company_name if company_name else "Unknown")
    final_sector = openai_data.get("sector", "Unknown")

    # 5️⃣ Проверяем, если это спам-домен
    if any(spam in (snippet or "").lower() for spam in spam_keywords) or final_company == "Unknown":
        final_country = "Test"
        final_sector = "Test"

    # Записываем финальный результат
    results[domain] = {
        "company": final_company,
        "country": final_country,
        "sector": final_sector
    }

    # Задержка для API (чтобы избежать блокировки)
    time.sleep(0.5)

# === ВЫВОД РЕЗУЛЬТАТОВ ===
print("\n🎯 Финальный результат:")
print(json.dumps(results, indent=4, ensure_ascii=False))


🔍 [1/195] Запрос для netsetsoftware.com...
🟢 Google нашел для netsetsoftware.com: NetSet Software Solutions
🟢 Whois нашел страну для netsetsoftware.com: UNITED STATES
📡 Отправка в OpenAI для netsetsoftware.com (country)...
🟢 OpenAI нашел country для netsetsoftware.com: India
📡 Отправка в OpenAI для netsetsoftware.com (company)...
🟢 OpenAI нашел company для netsetsoftware.com: NetSet Software
📡 Отправка в OpenAI для netsetsoftware.com (sector)...
🟢 OpenAI нашел sector для netsetsoftware.com: IT

🔍 [2/195] Запрос для skiff.com...
🟢 Google нашел для skiff.com: Skiff - Private, encrypted, secure email - 10 GB free
🟢 Whois нашел страну для skiff.com: UNITED STATES
📡 Отправка в OpenAI для skiff.com (country)...
🟢 OpenAI нашел country для skiff.com: United States
📡 Отправка в OpenAI для skiff.com (company)...
🟢 OpenAI нашел company для skiff.com: Skiff Technologies, Inc.
📡 Отправка в OpenAI для skiff.com (sector)...
🟢 OpenAI нашел sector для skiff.com: IT

🔍 [3/195] Запрос для agaseo.com...


In [276]:
# Данные для обновления
updates = {
    "laravel.com": ("USA", "Software Development"),
    "magtecsolutions.com": ("UAE", "Information Technology"),
    "patentsmarter.com": ("USA", "Legal Services"),
    "expertslides.com": ("Germany", "Information Technology"),
    "okadrian.com": ("Unknown", "Unknown"),
    "betranslated.com": ("Belgium", "Translation Services"),
    "provisionsinternational.com": ("USA", "Export Management"),
    "desightstudio.com": ("Germany", "Digital Agency"),
    "naastepad.com": ("USA", "Publishing"),
    "venturaix.com": ("Unknown", "Unknown"),
    "ncbhub.com": ("Norway", "Consulting Services"),
    "datafanatics.com": ("USA", "Web Design"),
    "solosyn.com": ("USA", "Pharmaceuticals"),
    "sousmedia.com": ("USA", "Software Development"),
    "suyen.com": ("Unknown", "Unknown"),
    "redrammedia.com": ("USA", "Media & Entertainment"),
    "team-genius.com": ("USA", "Sports Technology"),
    "dralias.com": ("Switzerland", "Cybersecurity"),
    "secure-otp.com": ("India", "Financial Technology"),
    "nextstepwebdesign.com": ("USA", "Web Design"),
    "passfwd.com": ("Switzerland", "Cybersecurity"),
    "cellbris.com": ("UAE", "Software Development"),
    "limitlessint.com": ("Jordan", "Unknown"),
    "indaco.com": ("USA", "Media & Entertainment"),
    "ispem.com": ("Italy", "Industrial Supplies"),
    "leadtagger.com": ("USA", "Online Marketing"),
    "cpiprint.com": ("USA", "Printing Services"),
    "onhires.com": ("USA", "Recruitment & Staffing"),
    "genesiprotection.com": ("Italy", "Industrial Safety"),
    "consultingfischer.com": ("Italy", "Consulting Services"),
    "odismanagement.com": ("USA", "Business Services"),
    "mztweb.com": ("Italy", "Blog"),
    "sourcingsegments.com": ("UK", "Recruitment"),
    "rocketstarmedia.com": ("USA", "Media & Entertainment"),
    "dobulk.com": ("Unknown", "Unknown"),
    "visualtronics.com": ("Italy", "Electronic Displays"),
    "absias.com": ("El Salvador", "Information Technology"),
    "maxinium.com": ("Unknown", "Unknown"),
    "natinnova.com": ("Spain", "Communication & Branding"),
    "digicybersec.com": ("Unknown", "Cybersecurity"),
    "adeptgraphics.com": ("Sweden/Italy", "Graphic Design"),
    "maxintegration.com": ("Unknown", "Unknown"),
    "xavadigital.com": ("New Zealand", "Web Design & Marketing"),
    "weeksoutstanding.com": ("UK", "Consulting"),
    "100-signals.com": ("Unknown", "Market Research"),
    "lightbolt.com": ("USA", "Unknown"),
    "incrementors.com": ("USA", "Digital Marketing"),
    "freilink.com": ("Unknown", "Unknown"),
    "contentleverage.com": ("USA", "Marketing"),
    "verycom.com": ("Unknown", "Digital Agency"),
    "novasu.com": ("USA", "Education"),
    "mindsharedigital.com": ("Unknown", "Digital Agency"),
    "iq310.com": ("USA", "Telecommunications"),
    "forezight.com": ("Denmark", "Consulting"),
    "consulta.com": ("Mexico", "News"),
    "thatleo.com": ("Unknown", "Blog"),
    "doordash.com": ("USA", "Food Delivery"),
    "adminas.com": ("USA", "Business Services"),
    "quantumdigitalplus.com": ("USA", "Digital Marketing"),
    "viralchilly.com": ("India", "Digital Marketing"),
    "somoseo.com": ("USA", "Web Design & SEO"),
    "extrainteger.com": ("Unknown", "Unknown"),
    "exdonuts.com": ("Unknown", "Unknown"),
    "rabbitex.com": ("Slovakia", "Agriculture"),
    "curuth.com": ("Unknown", "Unknown"),
    "peppydigital.com": ("USA", "Digital Marketing"),
    "wegastudios.com": ("Italy", "Web Design"),
    "embodee.com": ("USA", "Digital Products"),
    "fhblack.com": ("Canada", "Accounting Services"),
    "starlight-digital.com": ("USA", "Digital Marketing"),
}

# Обновление данных в results
for domain, (country, sector) in updates.items():
    if domain in results:
        results[domain]["country"] = country
        results[domain]["sector"] = sector

# Проверяем, что обновления прошли успешно
results_updated_df = pd.DataFrame.from_dict(results, orient="index")
results_updated_df

company  \
netsetsoftware.com                                                                     NetSet Software   
skiff.com                                                                     Skiff Technologies, Inc.   
agaseo.com                                                                                     Unknown   
eryod.com                                                                                      Unknown   
kravify.com                                                 kravify.com | verifymail.io Email Analysis   
em2lab.com                                                                                     Unknown   
buzblox.com                                                                                    Unknown   
splunk.com                                                                                 Splunk Inc.   
mac.com                                                                                     Apple Inc.   
luravell.com                                                                                   Unknown   
gate.com                                                                                      Gate.com   
egela.com                                                     egela.com | verifymail.io Email Analysis   
dalebig.com                                                                                    Unknown   
doolk.com                                                                                      Unknown   
devncie.com                                                 devncie.com | verifymail.io Email Analysis   
laravel.com                                               Laravel - The PHP Framework For Web Artisans   
kinsef.com                                                                                     Unknown   
cartep.com                                                                                     Unknown   
pismo.com                                                                        Pismo Tecnologia S.A.   
magtecsolutions.com                                                                   Magtec Solutions   
netsoil.com                                                                                    Unknown   
patentsmarter.com                                                                        PATENTsmarter   
degcos.com                                                   degcos.com | verifymail.io Email Analysis   
alterego.com                                                                           Alter Ego Italy   
expertslides.com                                                           ExpertSlides - ExpertSlides   
perfectlyimperfectdigital.com                                                                  Unknown   
clientamp.com                                                                                  Unknown   
okadrian.com                                 harold goldberg on X: "Happening right now, @OKAdrian ...   
sitesset.com                                                                                   Unknown   
betranslated.com                                                                          BeTranslated   
provisionsinternational.com              Provisions International, Inc. | An Export Management Company   
navigist.com                                                                                  Navigist   
desightstudio.com                                                                    desightstudio.com   
marchub.com                                                                                    Unknown   
naastepad.com                               Macroeconomics Beyond the NAIRU — Harvard University Press   
rainmakercommerce.com                                                                          Unknown   
gobizup.com                                                                                    Unknown   
venturaix.com                                                      

In [278]:
# Новые данные для обновления
additional_updates = {
    "okadrian.com": ("UK", "Music"),
    "venturaix.com": ("Denmark", "Investment Fund"),
    "suyen.com": ("Philippines", "Trade"),
    "limitlessint.com": ("USA", "Music"),
    "dobulk.com": ("USA/India", "Unknown"),
    "maxinium.com": ("Sri Lanka", "Digital Marketing"),
    "digicybersec.com": ("France", "IT Consulting"),
    "maxintegration.com": ("USA", "Technology"),
    "100-signals.com": ("Poland", "Marketing Analytics"),
    "lightbolt.com": ("USA", "Technology"),
    "freilink.com": ("Germany", "Marketing"),
    "verycom.com": ("India", "Creative Digital Agency"),
    "mindsharedigital.com": ("USA", "Marketing Agency"),
    "thatleo.com": ("India", "Marketing"),
    "extrainteger.com": ("Indonesia", "IT"),
    "exdonuts.com": ("Test", "Test"),
    "curuth.com": ("Test", "Test"),
}

# Обновление данных в results
for domain, (country, sector) in additional_updates.items():
    if domain in results:
        results[domain]["country"] = country
        results[domain]["sector"] = sector
    else:
        results[domain] = {"company": "Unknown", "country": country, "sector": sector}

# Вывод обновленных данных
results

{'netsetsoftware.com': {'company': 'NetSet Software',
  'country': 'India',
  'sector': 'IT'},
 'skiff.com': {'company': 'Skiff Technologies, Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'agaseo.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'eryod.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'kravify.com': {'company': 'kravify.com | verifymail.io Email Analysis',
  'country': 'Test',
  'sector': 'Test'},
 'em2lab.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'buzblox.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'splunk.com': {'company': 'Splunk Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'mac.com': {'company': 'Apple Inc.',
  'country': 'United States',
  'sector': 'Cosmetics'},
 'luravell.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'gate.com': {'company': 'Gate.com',
  'country': 'United States',
  'sector': 'IT'},
 'egela.com': {'company': 'egela.

In [281]:
# Обновление данных для dobulk.com
results["dobulk.com"] = {"company": "Unknown", "country": "India", "sector": "Footwear"}

# Вывод обновленных данных
results

{'netsetsoftware.com': {'company': 'NetSet Software',
  'country': 'India',
  'sector': 'IT'},
 'skiff.com': {'company': 'Skiff Technologies, Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'agaseo.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'eryod.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'kravify.com': {'company': 'kravify.com | verifymail.io Email Analysis',
  'country': 'Test',
  'sector': 'Test'},
 'em2lab.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'buzblox.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'splunk.com': {'company': 'Splunk Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'mac.com': {'company': 'Apple Inc.',
  'country': 'United States',
  'sector': 'Cosmetics'},
 'luravell.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'gate.com': {'company': 'Gate.com',
  'country': 'United States',
  'sector': 'IT'},
 'egela.com': {'company': 'egela.

In [293]:
# Словарь соответствий
mapping_dict = {
    "Test": "Test",
    "IT": "Technology",
    "Digital Marketing": "Marketing",
    "Marketing": "Marketing",
    "Media & Entertainment": "Media & Entertainment",
    "Software Development": "Technology",
    "Finance": "Finance & Investment",
    "Information Technology": "Technology",
    "Web Design": "Technology",
    "Technology": "Technology",
    "Telecommunications": "Technology",
    "Cosmetics": "Beauty",
    "Music": "Media & Entertainment",
    "Translation Services": "Human Resources",
    "Consulting Services": "Consulting",
    "Cybersecurity": "Technology",
    "Real Estate": "Real Estate",
    "Business Services": "Business Services",
    "Healthcare": "Healthcare & Insurance",
    "Education": "Education",
    "Consulting": "Consulting",
    "Legal Services": "Legal Services",
    "Export Management": "Government & Public Sector",
    "Digital Agency": "Marketing",
    "Publishing": "Media & Entertainment",
    "Investment Fund": "Finance & Investment",
    "Retail": "Retail & Food",
    "Logistics": "Logistics & Transportation Management",
    "Pharmaceuticals": "Healthcare & Insurance",
    "Trade": "Retail & Food",
    "Engineering": "Manufacturing & Chemicals",
    "Sports Technology": "Sports",
    "Financial Technology": "Finance & Investment",
    "Manufacturing": "Manufacturing & Chemicals",
    "Industrial Supplies": "Manufacturing & Chemicals",
    "Online Marketing": "Marketing",
    "Printing Services": "Manufacturing & Chemicals",
    "Recruitment & Staffing": "Human Resources",
    "Industrial Safety": "Manufacturing & Chemicals",
    "Dating Services": "Human Resources",
    "Construction": "Construction",
    "Blog": "Media & Entertainment",
    "Recruitment": "Human Resources",
    "Footwear": "Retail & Food",
    "Electronic Displays": "Technology",
    "Music Industry": "Media & Entertainment",
    "Communication & Branding": "Marketing",
    "IT Consulting": "Technology",
    "Graphic Design": "Art",
    "Automation and Instrumentation": "Technology",
    "Venture Capital": "Finance & Investment",
    "Web Design & Marketing": "Technology",
    "Arts and Entertainment": "Media & Entertainment",
    "Marketing Analytics": "Marketing",
    "Creative Digital Agency": "Marketing",
    "Marketing Agency": "Marketing",
    "Industrial Supply": "Manufacturing & Chemicals",
    "News": "Media & Entertainment",
    "Food Delivery": "Retail & Food",
    "Web Design & SEO": "Technology",
    "Furniture": "Retail & Food",
    "Agriculture": "Agriculture",
    "Digital Products": "Technology",
    "Accounting Services": "Finance & Investment",
    "Facilities Management": "Government & Public Sector",
    "Advertising Technology": "Marketing",
    "Logistics & Transportation Management": "Logistics & Transportation Management"
}

# Обновляем сектора в словаре
for domain, data in results.items():
    sector = data["sector"]
    results[domain]["sector"] = mapping_dict.get(sector, "Unknown")  # Если сектора нет в маппинге, ставим "Unknown"

# Проверяем обновленный список уникальных секторов
updated_sectors = set(data["sector"] for data in results.values())
updated_sectors

{'Agriculture',
 'Art',
 'Beauty',
 'Business Services',
 'Construction',
 'Consulting',
 'Education',
 'Finance & Investment',
 'Government & Public Sector',
 'Healthcare & Insurance',
 'Human Resources',
 'Legal Services',
 'Logistics & Transportation Management',
 'Manufacturing & Chemicals',
 'Marketing',
 'Media & Entertainment',
 'Real Estate',
 'Retail & Food',
 'Sports',
 'Technology',
 'Test'}

In [294]:
from collections import Counter

# Подсчет количества доменов по каждой стране и сектору
country_counts = Counter()
sector_counts = Counter()

for domain, data in results.items():
    country_counts[data["country"]] += 1
    sector_counts[data["sector"]] += 1

# Вывод количества доменов по странам
print("\nКоличество доменов по странам:")
for country, count in country_counts.most_common():
    print(f"{country}: {count}")

# Вывод количества доменов по секторам
print("\nКоличество доменов по секторам:")
for sector, count in sector_counts.most_common():
    print(f"{sector}: {count}")


Количество доменов по странам:
Test: 76
United States: 70
India: 8
Italy: 6
United Kingdom: 4
Germany: 3
UAE: 2
Denmark: 2
Malaysia: 2
Switzerland: 2
Canada: 2
Singapore: 2
Belgium: 1
Norway: 1
Philippines: 1
El Salvador: 1
Turkey: 1
Sri Lanka: 1
Spain: 1
France: 1
Australia: 1
Sweden: 1
North Macedonia: 1
New Zealand: 1
Poland: 1
Mexico: 1
Indonesia: 1
Slovakia: 1

Количество доменов по секторам:
Test: 76
Technology: 39
Marketing: 22
Media & Entertainment: 11
Finance & Investment: 7
Manufacturing & Chemicals: 6
Human Resources: 5
Retail & Food: 5
Consulting: 4
Healthcare & Insurance: 3
Beauty: 2
Government & Public Sector: 2
Logistics & Transportation Management: 2
Real Estate: 2
Business Services: 2
Education: 2
Legal Services: 1
Sports: 1
Construction: 1
Art: 1
Agriculture: 1


In [288]:
# Приведение всех значений "USA" к "United States" и "Sweden/Italy" к "Sweden"
for domain, data in results.items():
    if data["country"] == "USA":
        data["country"] = "United States"
    elif data["country"] == "Sweden/Italy":
        data["country"] = "Sweden"
    elif data["country"] == "UNITED STATES":
        data["country"] = "United States"
    elif data["country"] == "UK":
        data["country"] = "United Kingdom" 

# Вывод обновленных данных: 
results

{'netsetsoftware.com': {'company': 'NetSet Software',
  'country': 'India',
  'sector': 'IT'},
 'skiff.com': {'company': 'Skiff Technologies, Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'agaseo.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'eryod.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'kravify.com': {'company': 'kravify.com | verifymail.io Email Analysis',
  'country': 'Test',
  'sector': 'Test'},
 'em2lab.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'buzblox.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'splunk.com': {'company': 'Splunk Inc.',
  'country': 'United States',
  'sector': 'IT'},
 'mac.com': {'company': 'Apple Inc.',
  'country': 'United States',
  'sector': 'Cosmetics'},
 'luravell.com': {'company': 'Unknown', 'country': 'Test', 'sector': 'Test'},
 'gate.com': {'company': 'Gate.com',
  'country': 'United States',
  'sector': 'IT'},
 'egela.com': {'company': 'egela.

In [291]:
df_merged_updated_3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 21 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [292]:
unique_sectors = df_merged_updated_3["sector"].dropna().unique()
unique_sectors

array(['Technology', 'Finance & Investment', 'Education', 'Real Estate',
       'Media & Entertainment', 'Automotive', 'Human Resources',
       'Manufacturing & Chemicals', 'Legal Services', 'Construction',
       'Sports', 'Event Management', 'Travel & Hospitality', 'Test',
       'Healthcare & Insurance', 'Marketing',
       'Government & Public Sector', 'Beauty', 'Retail & Food', 'Art',
       'Fashion', 'Energy'], dtype=object)

In [295]:
# Вывод общего количества доменов в словаре
print(f"Общее количество доменов: {len(results)}\n")

# Вывод всех уникальных стран
unique_countries = set(entry["country"] for entry in results.values())
print(f"Уникальные страны ({len(unique_countries)}): {unique_countries}\n")

# Вывод всех уникальных секторов
unique_sectors = set(entry["sector"] for entry in results.values())
print(f"Уникальные сектора ({len(unique_sectors)}): {unique_sectors}\n")

# Вывод нескольких примеров записей
print("Примеры записей:")
for domain, info in list(results.items())[:10]:  # Вывести первые 10 записей
    print(f"{domain}: {info}")

Общее количество доменов: 195

Уникальные страны (28): {'UAE', 'New Zealand', 'Belgium', 'Malaysia', 'Sri Lanka', 'France', 'Sweden', 'Philippines', 'Canada', 'Slovakia', 'Indonesia', 'Switzerland', 'Denmark', 'Singapore', 'Germany', 'Spain', 'United States', 'Test', 'India', 'Norway', 'United Kingdom', 'Australia', 'Italy', 'Poland', 'North Macedonia', 'Mexico', 'Turkey', 'El Salvador'}

Уникальные сектора (21): {'Human Resources', 'Marketing', 'Legal Services', 'Consulting', 'Finance & Investment', 'Retail & Food', 'Manufacturing & Chemicals', 'Logistics & Transportation Management', 'Education', 'Art', 'Agriculture', 'Beauty', 'Test', 'Healthcare & Insurance', 'Sports', 'Technology', 'Media & Entertainment', 'Real Estate', 'Construction', 'Government & Public Sector', 'Business Services'}

Примеры записей:
netsetsoftware.com: {'company': 'NetSet Software', 'country': 'India', 'sector': 'Technology'}
skiff.com: {'company': 'Skiff Technologies, Inc.', 'country': 'United States', 'sect

In [299]:
# Создаем копию df_merged_updated_3, чтобы сохранить оригинальные данные
df_merged_updated_4 = df_merged_updated_3.copy()

# Обновляем значения в df_merged_updated_4 по данным из словаря results
df_merged_updated_4["sector"] = df_merged_updated_4["domain"].map(lambda d: results.get(d, {}).get("sector", df_merged_updated_4.loc[df_merged_updated_4["domain"] == d, "sector"].values[0]))
df_merged_updated_4["company_country"] = df_merged_updated_4["domain"].map(lambda d: results.get(d, {}).get("country", df_merged_updated_4.loc[df_merged_updated_4["domain"] == d, "company_country"].values[0]))

# Выводим количество обновленных записей
updated_sectors = df_merged_updated_4["sector"].notna().sum()
updated_countries = df_merged_updated_4["company_country"].notna().sum()

print(f"Обновлено секторов: {updated_sectors}")
print(f"Обновлено стран: {updated_countries}")

Обновлено секторов: 716
Обновлено стран: 716


In [301]:
# Подсчет количества доменов по каждой уникальной стране
country_counts = df_merged_updated_4["company_country"].value_counts()

# Подсчет количества доменов по каждому уникальному сектору
sector_counts = df_merged_updated_4["sector"].value_counts()

# Создаем DataFrame для удобного отображения
df_counts = pd.DataFrame({
    "Country": country_counts.index,
    "Domain Count (by Country)": country_counts.values
}).merge(
    pd.DataFrame({
        "Sector": sector_counts.index,
        "Domain Count (by Sector)": sector_counts.values
    }), how="outer", left_index=True, right_index=True
)

# Выводим таблицу с результатами
df_counts

Country  Domain Count (by Country)  \
0          United States                        279   
1                   Test                         99   
2                Germany                         50   
3            Switzerland                         32   
4         United Kingdom                         26   
5                  Italy                         23   
6              Australia                         22   
7                 Canada                         19   
8                  India                         16   
9             Luxembourg                         13   
10                Sweden                          9   
11           Netherlands                          8   
12                 Spain                          7   
13                France                          7   
14               Belgium                          7   
15  United Arab Emirates                          6   
16                Mexico                          5   
17             Singapore                          5   
18           New Zealand                          5   
19               Denmark                          5   
20          Saudi Arabia                          5   
21                 Japan                          4   
22                Poland                          4   
23               Vietnam                          3   
24                Turkey                          3   
25                Taiwan                          3   
26                Israel                          3   
27           Philippines                          3   
28                Norway                          3   
29               Ukraine                          3   
30                   UAE                          3   
31              Malaysia                          3   
32               Austria                          2   
33                 Chile                          2   
34          South Africa                          2   
35                 China                          2   
36        Czech Republic                          2   
37             Hong Kong                          1   
38           El Salvador                          1   
39                Belize                          1   
40             Indonesia                          1   
41              Colombia                          1   
42               Ecuador                          1   
43                  Iraq                          1   
44       North Macedonia                          1   
45                  Oman                          1   
46             Sri Lanka                          1   
47                Greece                          1   
48        European Union                          1   
49           Puerto Rico                          1   
50              Portugal                          1   
51                Russia                          1   
52                 Malta                          1   
53                 Kenya                          1   
54               Hungary                          1   
55                 Ghana                          1   
56                Cyprus                          1   
57               Comoros                          1   
58               Finland                          1   
59              Slovakia                          1   

                                   Sector  Domain Count (by Sector)  
0                              Technology                     277.0  
1                                    Test                      99.0  
2                               Marketing                      59.0  
3                    Finance & Investment                      47.0  
4                   Media & Entertainment                      37.0  
5                               Education                      36.0  
6                  Healthcare & Insurance                      29.0  
7                           Retail & Food                      23.0  
8               Manufacturing &

In [307]:
df_deactivated_licenses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 813 entries, 0 to 812
Data columns (total 11 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       813 non-null    int64  
 1   user_id                  551 non-null    float64
 2   license_key              813 non-null    object 
 3   prev_license_key         55 non-null     object 
 4   status                   813 non-null    object 
 5   tier                     736 non-null    float64
 6   plan_id                  813 non-null    object 
 7   appsumo_created_at       813 non-null    object 
 8   appsumo_event_timestamp  813 non-null    object 
 9   inserted_at              813 non-null    object 
 10  updated_at               813 non-null    object 
dtypes: float64(2), int64(1), object(8)
memory usage: 70.0+ KB


In [308]:
df_merged_updated_4.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 21 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [320]:
# Используем новый клиент OpenAI
from openai import OpenAI

client = OpenAI(api_key=OPENAI_API_KEY)  # Используем актуальный клиент

# Функция вызова OpenAI API с обработкой ошибок и лимитов
def call_openai(messages, retries=3, delay=10):
    for attempt in range(retries):
        try:
            response = client.chat.completions.create(
                model="gpt-3.5-turbo",
                messages=messages
            )
            return response.choices[0].message.content.strip()
        except openai.OpenAIError as e:
            print(f"⚠️ Ошибка OpenAI: {e}. Попытка {attempt + 1} из {retries}")
            if attempt < retries - 1:
                time.sleep(delay)  # Ждём перед повторным запросом
            else:
                return "Error"

# Создаем копию DataFrame перед обновлением
df_users_full_final = df_merged_updated_4.copy()
df_users_full_final["language"] = None  # Добавляем колонку для языка

# Фильтруем только строки, где вообще есть данные для анализа
df_filtered = df_users_full_final[
    (~df_users_full_final["feedback"].isna()) |
    (~df_users_full_final["system_message"].isna()) |
    (~df_users_full_final["company_country"].isna())
].copy()

# Обрезаем system_message до 500 символов (уменьшает потребление токенов)
df_filtered["system_message"] = df_filtered["system_message"].astype(str).str[:500]

# Обрабатываем батчами по 20 строк
batch_size = 20
total_batches = len(df_filtered) // batch_size + (1 if len(df_filtered) % batch_size > 0 else 0)

for batch_num in range(total_batches):
    start_idx = batch_num * batch_size
    end_idx = min((batch_num + 1) * batch_size, len(df_filtered))

    print(f"🔍 Обрабатываем строки {start_idx} - {end_idx}")

    batch_data = df_filtered.iloc[start_idx:end_idx]

    for idx, row in batch_data.iterrows():
        domain = row["domain"]
        country = row["company_country"]
        system_message = row["system_message"]
        feedback = row["feedback"]

        # Формируем контекст для OpenAI
        messages = [
            {"role": "system", "content": "Ты анализируешь язык пользователя на основе его страны, system_message и feedback."},
            {"role": "user", "content": f"""
                Дано:
                - Домен: {domain}
                - Страна: {country if pd.notna(country) else "Нет данных"}
                - System Message: {system_message if pd.notna(system_message) else "Нет данных"}
                - Feedback: {feedback if pd.notna(feedback) else "Нет данных"}

                Определи язык пользователя по правилам:
                1. Если есть feedback, используем его.
                2. Если feedback нет, но есть system_message и страна:
                   - Если system_message = страна → берем страну.
                   - Если system_message ≠ страна:
                     - Если страна многоязычная → берем system_message.
                     - Если страна одноязычная → берем страну.
                3. Если feedback и system_message нет:
                   - Если есть страна → берем страну.
                   - Если страна многоязычная, но system_message отсутствует → язык = None.
                   - Если нет ничего → язык = None.

                Ответ должен содержать только название языка без пояснений.
            """}
        ]

        # Запрашиваем OpenAI
        language = call_openai(messages)

        # Записываем результат в DataFrame
        df_users_full_final.at[idx, "language"] = language

    # Задержка для избежания лимитов API
    print(f"⏳ Завершен батч {batch_num + 1}/{total_batches}. Ожидание 10 секунд перед следующим...")
    time.sleep(10)

print("✅ Обработка завершена!")

🔍 Обрабатываем строки 0 - 20
⏳ Завершен батч 1/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 20 - 40
⏳ Завершен батч 2/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 40 - 60
⏳ Завершен батч 3/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 60 - 80
⏳ Завершен батч 4/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 80 - 100
⏳ Завершен батч 5/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 100 - 120
⏳ Завершен батч 6/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 120 - 140
⏳ Завершен батч 7/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 140 - 160
⏳ Завершен батч 8/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 160 - 180
⏳ Завершен батч 9/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 180 - 200
⏳ Завершен батч 10/102. Ожидание 10 секунд перед следующим...
🔍 Обрабатываем строки 200 - 220
⏳ Завершен батч 11/102. Ожидание 10 секунд пере

In [321]:
df_users_full_final[df_users_full_final["language"].notna()][["domain", "company_country", "language"]].head(100)

domain       company_country        language
0                   gmail.com                  None      Английский
1                   gmail.com                  None      Английский
3                   orbita.vc            Luxembourg     Французский
6                   gmail.com                  None      Английский
8                       3f.lu            Luxembourg   Luxembourgish
9                   gmail.com                  None         Русский
11                      pm.me                  None        Немецкий
12                 seturon.io         United States         English
14          zentrapreneur.com         United States         English
19                  gmail.com                  None      Английский
23                  gmail.com                  None      Английский
34                  gmail.com                  None     Французский
36                upthrust.eu        European Union      Английский
40                keeprise.ru                Russia         Russian
58                  gmail.com                  None         Русский
84                mostfund.vc         United States         English
104  colegiosantamaria.edu.mx                Mexico       Испанский
110          oasisdemaadi.com         United States      Английский
115                 gmail.com                  None      Английский
122            goodnoze.co.nz           New Zealand         English
162        netsetsoftware.com                 India           Hindi
170                 skiff.com         United States         English
211                  pismo.ai         United States         English
277         printagram.com.mt                 Malta         Maltese
285                st.uew.edu                 Ghana      Английский
291                 orbita.vc            Luxembourg     Французский
304                 orbita.vc            Luxembourg     Французский
315                 orbita.vc            Luxembourg     Французский
327                 orbita.vc            Luxembourg           Иврит
337            wilscott.co.za          South Africa      Английский
339           spd-ukraine.com               Ukraine      Украинский
340           spd-ukraine.com               Ukraine      Украинский
341           spd-ukraine.com               Ukraine      Украинский
343               8shield.net         United States      Английский
352                agaseo.com                  Test            None
353                 eryod.com                  Test            None
354                acname.com         United States         English
355                 eryod.com                  Test            None
357               kravify.com                  Test            None
366                em2lab.com                  Test   Не определен.
367               buzblox.com                  Test            None
373               luxtoday.lu            Luxembourg  Люксембургский
388                   mail.ru                  None         Русский
391                splunk.com         United States      Английский
394                   mac.com         United States         English
396                seturon.io         United States      Английский
397                    skl.vc         United States         English
398              luravell.com                  Test            None
399                  gate.com         United States         English
401              luravell.com                  Test            None
402                seturon.io         United States         English
408                seturon.io         United States      Английский
409                seturon.io         United States      Английский
410                 egela.com                  Test            Тест
419                seturon.io         United States         English
420                seturon.io         United States         English
424                 egela.com                  Test            None
425               dalebig.com                  Test      Английский
433        

In [322]:
# Выводим уникальные языки
unique_languages = df_users_full_final["language"].dropna().unique()

# Отображаем список уникальных языков
unique_languages

array(['Английский', 'Французский', 'Luxembourgish', 'Русский',
       'Немецкий', 'English', 'Russian', 'Испанский', 'Hindi', 'Maltese',
       'Иврит', 'Украинский', 'None', 'Не определен.', 'Люксембургский',
       'Тест', 'Арабский', 'German', 'Spanish', 'Малайский', 'Греческий',
       'Суахили', 'Японский', 'Польский', 'Английский.', 'Hawaiian',
       'Hebrew', 'Кантонский', 'Итальянский', 'Испанский (Испания)',
       'Корейский', 'Китайский', 'Vietnamese', 'Finnish', 'Шведский',
       'Телугу', 'Болгарский', 'Tiếng Việt', 'Вьетнамский',
       'Английский (Великобритания)', 'Dutch', 'Румынский', 'Polish',
       'Arabic', 'Португальский', 'British English', 'Английский (США)',
       'Датский', 'Нидерландский', 'Norwegian',
       'Португальский (Бразилия)', 'Венгерский', 'South African English',
       'Italian', 'Brazilian Portuguese', 'Словенский', 'Турецкий',
       'Урду', 'isiXhosa', 'Test', 'Chinese', 'Мандаринского.', 'Хинди',
       'Japanese', '한국어', 'Словацкий', 'К

In [324]:
# Создаем маппинг для исправления значений
language_corrections = {
    "Klingon": "Test",
    "Duits, Italiaans, Nederlands.": "English",
    "Markdown": "English"
}

# Обновляем значения в колонке "language"
df_users_full_final["language"] = df_users_full_final["language"].replace(language_corrections)

print("✅ Ошибки исправлены, языки приведены к английскому написанию.")

✅ Ошибки исправлены, языки приведены к английскому написанию.


In [327]:
# Обновляем значения в DataFrame
df_users_full_final.loc[
    df_users_full_final["language"] == "Português, испанский, итальянский, тайский, турецкий.", 
    ["sector", "company_country", "language"]
] = ["Education", "United States", "English"]

id                      domain          inserted_at  \
12      29                  seturon.io  2023-08-31 10:18:12   
14      35           zentrapreneur.com  2023-09-13 19:54:36   
84     108                 mostfund.vc  2023-10-06 03:10:14   
122    146              goodnoze.co.nz  2023-10-17 02:53:00   
170    194                   skiff.com  2023-10-23 15:44:23   
211    236                    pismo.ai  2023-11-03 10:10:12   
354    380                  acname.com  2024-04-18 08:41:49   
394    422                     mac.com  2024-06-12 15:30:06   
397    425                      skl.vc  2024-06-19 10:45:02   
399    427                    gate.com  2024-06-19 12:28:50   
402    430                  seturon.io  2024-06-20 14:26:23   
419    447                  seturon.io  2024-06-23 08:10:38   
420    448                  seturon.io  2024-06-23 08:10:47   
433    461               annardltd.com  2024-06-26 04:03:05   
441    469                  seturon.io  2024-06-26 08:51:14   
483    512                  seturon.io  2024-07-01 16:42:25   
505    534                  seturon.io  2024-07-03 11:56:20   
510    539                  seturon.io  2024-07-03 15:02:58   
511    540                 laravel.com  2024-07-04 04:55:55   
517    546                  seturon.io  2024-07-05 11:16:14   
524    553                  seturon.io  2024-07-08 07:23:07   
526    555                  seturon.io  2024-07-08 07:23:25   
527    556                  seturon.io  2024-07-08 07:23:32   
528    557                  seturon.io  2024-07-08 07:23:42   
529    558                  seturon.io  2024-07-08 07:24:01   
533    562                  seturon.io  2024-07-09 12:27:24   
570    599                   cogeco.ca  2024-07-19 12:56:21   
591    620                   gmail.com  2024-07-22 05:23:41   
751    780                     mac.com  2024-07-27 16:29:26   
918    948              winterkids.org  2024-09-16 14:21:18   
939    971           patentsmarter.com  2024-09-16 17:27:20   
1040  1078        trumanpublishing.com  2024-09-17 16:28:28   
1043  1081           voominsurance.com  2024-09-17 17:37:48   
1068  1108                   gmail.com  2024-09-18 02:04:16   
1106  1147                   gmail.com  2024-09-18 19:15:50   
1110  1152                okadrian.com  2024-09-18 20:00:21   
1124  1167                 hotmail.com  2024-09-18 20:59:39   
1133  1176                   gmail.com  2024-09-18 23:07:07   
1135  1178            philkurth.com.au  2024-09-18 23:23:55   
1138  1181             frysteen.com.au  2024-09-18 23:58:51   
1145  1188                   gmail.com  2024-09-19 01:50:37   
1160  1204                   gmail.com  2024-09-19 04:27:55   
1201  1247                   gmail.com  2024-09-19 10:08:57   
1216  1263                 outlook.com  2024-09-19 12:43:09   
1237  1286                   gmail.com  2024-09-19 14:34:19   
1271  1322           cornercapital.com  2024-09-19 18:25:32   
1287  1338               naastepad.com  2024-09-19 21:03:39   
1290  1341                     mac.com  2024-09-19 21:49:02   
1321  1373                   gmail.com  2024-09-20 02:44:49   
1323  1375                   gmail.com  2024-09-20 02:55:53   
1336  1389              eleuhealth.com  2024-09-20 06:02:06   
1350  1405                   gmail.com  2024-09-20 09:41:01   
1368  1423                 gobizup.com  2024-09-20 12:56:30   
1375  1431               venturaix.com  2024-09-20 14:28:46   
1382  1438             creatorways.com  2024-09-20 15:11:47   
1405  1462                 tennflexpro  2024-09-20 17:44:44   
1409  1466                   gmail.com  2024-09-20 17:59:54   
1417  1474         royalassistants.com  2024-09-20 18:42:39   
1437  1494                 tazlink.com  2024-09-20 22:53:03   
1456  1515            datafanatics.com  2024-09-21 03:01:09   
1479  1540                   gmail.com  2024-09-21 07:58:41   
1491  1553                   gmail.com  2024-09-21 10:40:35   
1494  1556                  shafra.com 

In [328]:
# Обновляем французский язык
df_users_full_final.loc[df_users_full_final["language"].isin(
    ["Французский", "French", "Французский (French)", "Французский."]
), "language"] = "French"

# Обновляем немецкий язык
df_users_full_final.loc[df_users_full_final["language"].isin(
    ["Немецкий", "German", "Deutsch", "GERMAN", "Немецкий (German)"]
), "language"] = "German"

# Обновляем итальянский язык
df_users_full_final.loc[df_users_full_final["language"].isin(
    ["Итальянский", "Italian", "Italiano", "Итальянский."]
), "language"] = "Italian"

# Обновляем японский язык
df_users_full_final.loc[df_users_full_final["language"] == "Язык пользователя: Японский", "language"] = "Japanese"

# Выводим уникальные значения после обновления для проверки
df_users_full_final["language"].unique()

array(['Английский', None, 'French', 'Luxembourgish', 'Русский', 'German',
       'English', 'Russian', 'Испанский', 'Hindi', 'Maltese', 'Иврит',
       'Украинский', 'None', 'Не определен.', 'Люксембургский', 'Тест',
       'Арабский', 'Spanish', 'Малайский', 'Греческий', 'Суахили',
       'Японский', 'Польский', 'Английский.', 'Hawaiian', 'Hebrew',
       'Кантонский', 'Italian', 'Испанский (Испания)', 'Корейский',
       'Китайский', 'Vietnamese', 'Finnish', 'Шведский', 'Телугу',
       'Болгарский', 'Tiếng Việt', 'Вьетнамский',
       'Английский (Великобритания)', 'Dutch', 'Румынский', 'Polish',
       'Arabic', 'Португальский', 'British English', 'Английский (США)',
       'Датский', 'Нидерландский', 'Norwegian',
       'Португальский (Бразилия)', 'Венгерский', 'South African English',
       'Brazilian Portuguese', 'Словенский', 'Турецкий', 'Урду',
       'isiXhosa', 'Test', 'Chinese', 'Мандаринского.', 'Хинди',
       'Japanese', '한국어', 'Словацкий', 'Китайский (Simple Chinese)'

In [329]:
# Проверяем, существует ли DataFrame
if 'df_users_full_final' in locals():
    # Словарь замен для приведения языков к английскому написанию
    language_replacements = {
        # Spanish
        'Испанский': 'Spanish', 'Spanish': 'Spanish', 'Испанский (Испания)': 'Spanish',
        'Spanish Mexico': 'Spanish', 'Spanish LATAM': 'Spanish', 'Español': 'Spanish',
        'испанский': 'Spanish', 'Spanish, Traditional Chinese': 'Spanish',

        # Italian
        'Итальянский': 'Italian', 'Italian': 'Italian', 'Italiano': 'Italian', 'Italian.': 'Italian',

        # Portuguese
        'Португальский': 'Portuguese', 'Português de Portugal': 'Portuguese', 'Европейский португальский.': 'Portuguese',
        'Brazilian Portuguese': 'Brazilian Portuguese', 'Португальский (Бразилия)': 'Brazilian Portuguese',
        'Бразильский Португальский': 'Brazilian Portuguese', 'Бразильский португальский': 'Brazilian Portuguese',

        # Vietnamese
        'Вьетнамский': 'Vietnamese', 'Vietnamese': 'Vietnamese', 'Tiếng Việt': 'Vietnamese', 'Вьетнамский.': 'Vietnamese',

        # Romanian
        'Румынский': 'Romanian', 'Romanian': 'Romanian',

        # Polish
        'Польский': 'Polish', 'Polish': 'Polish', 'польский': 'Polish', 'Польский (Polish)': 'Polish', 'Polski': 'Polish',

        # Turkish
        'Турецкий': 'Turkish', 'Turkish': 'Turkish',

        # Ukrainian
        'Украинский': 'Ukrainian', 'Ukrainian': 'Ukrainian', 'Українська': 'Ukrainian',

        # Unknown
        'Не определен.': 'Unknown', 'Язык пользователя: None': 'Unknown', 'None': 'Unknown',

        # Test
        'Тест': 'Test', 'Test': 'Test',

        # Japanese
        'Язык пользователя: Японский': 'Japanese', 'Японский': 'Japanese', 'Японский.': 'Japanese',

        # Hindi
        'Хинди': 'Hindi', 'Hindi': 'Hindi',

        # Finnish
        'Финский': 'Finnish',

        # Swedish
        'Шведский': 'Swedish',

        # Danish
        'Датский': 'Danish',

        # Dutch
        'Нидерландский': 'Dutch',

        # Norwegian
        'Норвежский': 'Norwegian',

        # Croatian
        'Хорватский': 'Croatian',

        # Macedonian
        'Македонский': 'Macedonian',

        # Armenian
        'Армянский': 'Armenian',

        # Mongolian
        'Монголский': 'Mongolian',

        # Bosnian
        'Боснийский': 'Bosnian',

        # Multiple languages → English
        'Португальский, испанский, итальянский, тайский, турецкий.': 'English'
    }

    # Применяем замену
    df_users_full_final['language'] = df_users_full_final['language'].replace(language_replacements)

    print("✅ Languages have been standardized to English notation.")
else:
    print("❌ DataFrame df_users_full_final not found.")

✅ Languages have been standardized to English notation.


In [332]:
# Обновляем страну для South African English → South Africa
df_users_full_final.loc[
    (df_users_full_final["language"] == "English (South African)"),
    "company_country"
] = "South Africa"

# Обновляем страну для Australian English → Australia
df_users_full_final.loc[
    (df_users_full_final["language"] == "English (Australian)"),
    "company_country"
] = "Australia"

print("✅ Обновление стран завершено.")

✅ Обновление стран завершено.


In [333]:
# Создаем соответствие между старыми и новыми названиями языков
language_mapping = {
    "Русский": "Russian",
    "Иврит": "Hebrew",
    "Люксембургский": "Luxembourgish",
    "Малайский": "Malay",
    "Греческий": "Greek",
    "Суахили": "Swahili",
    "Телугу": "Telugu",
    "Болгарский": "Bulgarian",
    "Английский (Великобритания)": "English",
    "Английский (США)": "English",
    "Венгерский": "Hungarian",
    "Словенский": "Slovenian",
    "Урду": "Urdu",
    "Китайский": "Chinese",
    "Мандаринского.": "Mandarin Chinese",
    "한국어": "Korean",
    "Словацкий": "Slovak",
    "Китайский (Simple Chinese)": "Simplified Chinese",
    "Индонезийский": "Indonesian",
    "Китайский (упрощенный)": "Simplified Chinese",
    "Китайский (Традиционный)": "Traditional Chinese",
    "Традиционный китайский": "Traditional Chinese",
    "Тамильский": "Tamil",
    "Филиппинский (Tagalog)": "Tagalog",
    "Язык: Японский": "Japanese",
    "Испанский.": "Spanish",
    "Гуджарати": "Gujarati",
    "Тайский": "Thai",
    "Швейцарский английский": "Swiss English",
    "Китайский.": "Chinese",
    "Чешский": "Czech",
    "Филиппинский": "Filipino",
    "繁體中文": "Traditional Chinese",
    "Английский (US)": "English",
    "Литовский": "Lithuanian",
    "Bengali": "Bengali",
    "Macedonian": "Macedonian",
    "Hispanic": "Spanish"  # Hispanic - этническая группа, заменяем на Spanish
}

# Применяем замену в DataFrame
df_users_full_final["language"] = df_users_full_final["language"].replace(language_mapping)

In [335]:
# Словарь для замены значений
language_corrections = {
    "Арабский": "Arabic",
    "Кантонский": "Cantonese",
    "Корейский": "Korean",
    "Китайский (Chinese)": "Chinese",
    "Бенгальский": "Bengali",
    "Непальский": "Nepali",
    "Монгольский": "Mongolian",
    "Английский (сленг)": "English",
    "Английский (English)": "English",
    "Английский.": "English",
    "English.": "English",
    "английский": "English",
    "Китайский (繁體中文)": "Traditional Chinese",
    "简体中文": "Simplified Chinese",
    "Indonesian.": "Indonesian"
}

# Применяем исправления в колонке "language"
df_users_full_final["language"] = df_users_full_final["language"].replace(language_corrections)

In [337]:
df_users_full_final["language"] = df_users_full_final["language"].replace({
    "Английский": "English",
    "Simple Chinese": "Simplified Chinese"
})

In [338]:
df_users_full_final["language"].unique()

array(['English', None, 'French', 'Luxembourgish', 'Russian', 'German',
       'Spanish', 'Hindi', 'Maltese', 'Hebrew', 'Ukrainian', 'Unknown',
       'Test', 'Arabic', 'Malay', 'Greek', 'Swahili', 'Japanese',
       'Polish', 'Hawaiian', 'Cantonese', 'Italian', 'Korean', 'Chinese',
       'Vietnamese', 'Finnish', 'Swedish', 'Telugu', 'Bulgarian', 'Dutch',
       'Romanian', 'Portuguese', 'British English', 'Danish', 'Norwegian',
       'Brazilian Portuguese', 'Hungarian', 'South African English',
       'Slovenian', 'Turkish', 'Urdu', 'isiXhosa', 'Mandarin Chinese',
       'Slovak', 'Simplified Chinese', 'Indonesian', 'Bengali',
       'Traditional Chinese', 'Tamil', 'Bahasa Indonesia', 'Tagalog',
       'Thai', 'Gujarati', 'Bosnian', 'Nepali', 'Croatian',
       'Swiss English', 'Khmer', 'Czech', 'Australian English',
       'Filipino', 'JavaScript', 'Mongolian', 'Armenian', 'Macedonian',
       'Traditional Chinese (Taiwan)', 'Amharic', 'Marathi', 'Lithuanian'],
      dtype=object)

In [340]:
df_users_full_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 22 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [342]:
# Сохраняем DataFrame в CSV в текущую директорию
csv_filename = "df_users_full_final.csv"
df_users_full_final.to_csv(csv_filename, index=False, encoding="utf-8")

print(f"✅ Файл сохранен в текущую папку: {csv_filename}")

✅ Файл сохранен в текущую папку: df_users_full_final.csv


In [354]:
import pandas as pd

# Создаем DataFrame с обновленными значениями
update_data = [
    (44, "Russia", "Russian", "Business Services"),
    (111, "Unknown", "English", "Media & Entertainment"),
    (133, "Estonia", "Estonian", "Business Services"),
    (191, "Unknown", "English", "Education"),
    (356, "Unknown", "English", "Business Services"),
    (358, "Unknown", "English", "Media & Entertainment"),
    (368, "Unknown", "English", "Media & Entertainment"),
    (400, "Unknown", "English", "Technology"),
    (429, "South Korea", "Korean", "Retail & Food"),
    (437, "Unknown", "Russian", "Business Services"),
    (455, "Unknown", "Russian", "Business Services"),
    (486, "Unknown", "Russian", "Business Services"),
    (514, "India", "English", "Government & Public Sector"),
    (519, "Unknown", "English", "Retail & Food"),
    (590, "Canada", "English", "Technology"),
    (719, "Australia", "English", "Media & Entertainment"),
    (844, "USA", "English", "Technology"),
    (912, "USA", "English", "Technology"),
    (918, "USA", "English", "Non-Profit"),
    (935, "Unknown", "English", "Technology"),
    (967, "Unknown", "English", "Business Services"),
    (973, "USA", "English", "Technology"),
    (975, "Unknown", "English", "Media & Entertainment"),
    (976, "USA", "English", "Legal Services"),
    (993, "Finland", "Finnish", "Business Services"),
    (1014, "Unknown", "English", "Marketing"),
    (1023, "Mexico", "Spanish", "Media & Entertainment"),
    (1033, "Germany", "German", "Business Services"),
    (1042, "USA", "English", "Healthcare & Insurance"),
    (1044, "Spain", "Spanish", "Business Services"),
    (1049, "USA", "English", "Marketing"),
    (1059, "USA", "English", "Non-Profit"),
    (1066, "Romania", "Romanian", "Business Services"),
    (1091, "USA", "English", "Finance & Investment"),
    (1100, "Kazakhstan", "Russian", "Business Services"),
    (1107, "Gibraltar", "English", "Marketing"),
    (1115, "Germany", "German", "Media & Entertainment"),
    (1140, "Ireland", "English", "Marketing"),
    (1146, "Indonesia", "Indonesian", "Education"),
    (1147, "USA", "English", "Sports"),
    (1149, "South Korea", "Korean", "Technology"),
    (1163, "UK", "English", "Media & Entertainment"),
    (1171, "Unknown", "Spanish", "Business Services"),
    (1178, "Estonia", "English", "Consulting"),
    (1198, "Bulgaria", "Bulgarian", "Technology"),
    (1204, "Australia", "English", "Consulting"),
    (1207, "Italy", "Italian", "Technology"),
    (1209, "Sweden", "Swedish", "Consulting"),
    (1232, "USA", "English", "Retail & Food"),
    (1243, "Unknown", "English", "Technology"),
    (1246, "Italy", "Italian", "Business Services"),
    (1248, "Estonia", "English", "Technology"),
    (1253, "Estonia", "English", "Beauty"),
    (1258, "Thailand", "Thai", "Healthcare & Insurance"),
    (1261, "Germany", "German", "Media & Entertainment"),
    (1262, "Unknown", "English", "Technology"),
    (1264, "Unknown", "English", "Business Services"),
    (1265, "Unknown", "English", "Marketing"),
    (1269, "Unknown", "English", "Business Services"),
    (1317, "USA", "English", "Education"),
    (1332, "Canada", "English", "Business Services"),
    (1366, "Germany", "German", "Business Services"),
    (1370, "Slovakia", "Slovak", "Marketing"),
    (1376, "Netherlands", "English", "Technology"),
    (1402, "Canada", "English", "Consulting"),
    (1403, "Finland", "Finnish", "Business Services"),
    (1412, "Finland", "Finnish", "Business Services"),
    (1414, "USA", "English", "Retail & Food"),
    (1432, "Germany", "German", "Business Services"),
    (1447, "USA", "English", "Consulting"),
    (1449, "USA", "English", "Business Services"),
    (1450, "USA", "English", "Marketing"),
    (1451, "USA", "English", "Consulting"),
    (1453, "Unknown", "English", "Business Services"),
    (1496, "USA", "English", "Consulting"),
    (1518, "USA", "English", "Healthcare & Insurance"),
    (1546, "Canada", "English", "Retail & Food"),
    (1548, "Canada", "English", "Marketing"),
    (1551, "Canada", "English", "Business Services"),
    (1593, "Netherlands", "Dutch", "Business Services"),
    (1601, "Netherlands", "Dutch", "Business Services"),
    (1623, "Japan", "Japanese", "Finance & Investment"),
    (1631, "Bulgaria", "Bulgarian", "Technology"),
    (1638, "Ireland", "English", "Technology"),
    (1654, "China", "Chinese", "Consulting"),
    (1668, "Austria", "German", "Tourism"),
    (1673, "USA", "English", "Technology"),
    (1680, "Japan", "Japanese", "Business Services"),
    (1717, "Italy", "Italian", "Business Services"),
    (1740, "India", "Gujarati", "Education"),
    (1749, "Spain", "Spanish", "Business Services"),
    (1772, "South Korea", "Korean", "Education"),
    (1773, "Poland", "Polish", "Business Services"),
    (1776, "Unknown", "Unknown", "Business Services"),
    (1786, "Germany", "German", "Business Services"),
    (1889, "USA", "English", "Non-Profit"),
    (1927, "Germany", "German", "Business Services"),
    (1931, "Sweden", "Swedish", "Business Services"),
    (1972, "India", "English", "Non-Profit"),
    (1997, "China", "English", "Education"),
    (2026, "USA", "English", "Healthcare & Insurance"),
    (2048, "Canada", "English", "Business Services"),
    (2054, "Poland", "Polish", "Sports"),
    (2057, "Poland", "Polish", "Sports"),
    (2094, "China", "Chinese", "Business Services"),
    (2143, "Canada", "English", "Business Services"),
    (2169, "Germany", "German", "Government & Public Sector"),
    (2171, "Unknown", "Spanish", "Consulting"),
    (2181, "Germany", "German", "Business Services"),
]


In [355]:
import pandas as pd

# Функция для обновления значений, если в df_update не "Unknown" и не None
def safe_update(row, update_row):
    for col in ["company_country", "language", "sector"]:
        if pd.isna(row[col]) or row[col] in [None, "Unknown"]:  # Только если текущее значение пустое
            row[col] = update_row[col]
    return row

# Преобразуем update_data в DataFrame
df_update = pd.DataFrame(update_data, columns=["id", "company_country", "language", "sector"])

# Устанавливаем id как индекс для быстрого обновления
df_update.set_index("id", inplace=True)

# Применяем обновление с проверкой
df_users_full_final.update(df_users_full_final.loc[df_update.index].apply(
    lambda row: safe_update(row, df_update.loc[row.name]), axis=1
))

# Проверяем изменения
print(df_users_full_final.loc[df_update.index, ["company_country", "language", "sector"]])

     company_country            language                      sector
id                                                                  
44            Russia             Russian           Business Services
111          Unknown             English       Media & Entertainment
133          Estonia            Estonian           Business Services
191          Unknown             English                   Education
356          Unknown             English           Business Services
358          Unknown             English       Media & Entertainment
368          Unknown             English       Media & Entertainment
400          Unknown             English                  Technology
429      South Korea              Korean               Retail & Food
437          Unknown             Russian           Business Services
455          Unknown             Russian           Business Services
486          Unknown             Russian           Business Services
514            India             E

In [363]:
df_users_full_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 22 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   total_paid             4946 non-null   float64
 10  currency_code          3177 non-null   object 
 11  user_agent             4381 non-null   object 
 12  system_message         1199 non-null   object 
 13  tier                   551 non-null    float64
 14  reason                 541 non-null    object 
 15  feed

In [362]:
df_licenses = pd.read_csv("/Users/user/Pismo/pismo_deactivated_licenses.csv")
df_licenses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 813 entries, 0 to 812
Data columns (total 11 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       813 non-null    int64  
 1   user_id                  551 non-null    float64
 2   license_key              813 non-null    object 
 3   prev_license_key         55 non-null     object 
 4   status                   813 non-null    object 
 5   tier                     736 non-null    float64
 6   plan_id                  813 non-null    object 
 7   appsumo_created_at       813 non-null    object 
 8   appsumo_event_timestamp  813 non-null    object 
 9   inserted_at              813 non-null    object 
 10  updated_at               813 non-null    object 
dtypes: float64(2), int64(1), object(8)
memory usage: 70.0+ KB


In [364]:
# Добавляем колонку total_paid с условиями
df_licenses["total_paid"] = df_licenses["tier"].map({1: 8.775, 2: 24.525})

# Выводим результат
print(df_licenses[["tier", "total_paid"]].dropna().head())

   tier  total_paid
0   1.0       8.775
1   1.0       8.775
2   1.0       8.775
3   2.0      24.525
4   1.0       8.775


In [365]:
df_licenses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 813 entries, 0 to 812
Data columns (total 12 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       813 non-null    int64  
 1   user_id                  551 non-null    float64
 2   license_key              813 non-null    object 
 3   prev_license_key         55 non-null     object 
 4   status                   813 non-null    object 
 5   tier                     736 non-null    float64
 6   plan_id                  813 non-null    object 
 7   appsumo_created_at       813 non-null    object 
 8   appsumo_event_timestamp  813 non-null    object 
 9   inserted_at              813 non-null    object 
 10  updated_at               813 non-null    object 
 11  total_paid               736 non-null    float64
dtypes: float64(3), int64(1), object(8)
memory usage: 76.3+ KB


In [370]:
# Объединяем данные, используя user_id из df_licenses и id из df_users_full_final
df_users_licenses_final = df_users_full_final.merge(
    df_licenses[["user_id", "status", "tier", "total_paid"]],
    left_on="id", right_on="user_id", how="left"
)

# Создаем колонку status, если ее не было
if "status" not in df_users_full_final.columns:
    df_users_licenses_final["status"] = df_users_licenses_final["status"]
else:
    df_users_licenses_final["status"] = df_users_licenses_final["status"].combine_first(df_users_full_final["status"])

# Обновляем tier и total_paid только там, где изначальное значение NaN или 0
df_users_licenses_final["tier"] = df_users_licenses_final["tier_x"].where(
    df_users_licenses_final["tier_x"].notna() & (df_users_licenses_final["tier_x"] != 0),
    df_users_licenses_final["tier_y"]
)

df_users_licenses_final["total_paid"] = df_users_licenses_final["total_paid_x"].where(
    df_users_licenses_final["total_paid_x"].notna() & (df_users_licenses_final["total_paid_x"] != 0),
    df_users_licenses_final["total_paid_y"]
)

# Удаляем лишние столбцы
df_users_licenses_final.drop(columns=["user_id", "tier_x", "tier_y", "total_paid_x", "total_paid_y"], inplace=True, errors="ignore")

# Вывод результата
df_users_licenses_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4946 entries, 0 to 4945
Data columns (total 23 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     4946 non-null   int64  
 1   domain                 4946 non-null   object 
 2   inserted_at            4946 non-null   object 
 3   updated_at             4946 non-null   object 
 4   paid_till              4843 non-null   object 
 5   had trial              4946 non-null   bool   
 6   in_trial               4946 non-null   bool   
 7   canceled_subscription  4946 non-null   bool   
 8   app_version            3191 non-null   object 
 9   currency_code          3177 non-null   object 
 10  user_agent             4381 non-null   object 
 11  system_message         1199 non-null   object 
 12  reason                 541 non-null    object 
 13  feedback               525 non-null    object 
 14  browser                4381 non-null   object 
 15  os  

In [371]:
df_users_licenses_final["domain_type"].unique()

array(['public', 'corporate', 'unknown'], dtype=object)

In [372]:
# Определяем нужные колонки для сохранения
columns_to_save = [
    "id", "domain", "inserted_at", "updated_at", "paid_till", 
    "had trial", "in_trial", "canceled_subscription", "app_version", 
    "currency_code", "feedback", "browser", "os", "sector", 
    "company_country", "language", "status", "tier", "total_paid"
]

# Создаем DataFrame только с нужными колонками
df_filtered = df_users_licenses_final[columns_to_save]

# Сохраняем в PKL
df_filtered.to_pickle("df_users_licenses_final.pkl")

# Сохраняем в CSV
df_filtered.to_csv("df_users_licenses_final.csv", index=False)

print("Файлы df_users_licenses_final.pkl и df_users_licenses_final.csv успешно сохранены.")

Файлы df_users_licenses_final.pkl и df_users_licenses_final.csv успешно сохранены.
